# Personalized Information Retrieval

SE-PQA (Stack Exchange Personalized Question-Answering) collects a large amount of questions and answers, along with rich users' features, for the purpose of community question answering (cQA). The contextual and user-related information can be useful to introduce personalization in the search engine.

https://zenodo.org/records/10679181


In [ ]:
!gdown 1HhgXzyEpsZNcenU9XhJuOYyDUKEzUse4

Downloading...
From (original): https://drive.google.com/uc?id=1HhgXzyEpsZNcenU9XhJuOYyDUKEzUse4
From (redirected): https://drive.google.com/uc?id=1HhgXzyEpsZNcenU9XhJuOYyDUKEzUse4&confirm=t&uuid=e289d456-9fac-4428-aeaf-b8cbe3d60fa8
To: /content/pir_data.zip
100% 3.30G/3.30G [01:10<00:00, 46.7MB/s]


In [ ]:
!unzip pir_data.zip

Archive:  pir_data.zip
   creating: PIR_data/
  inflating: PIR_data/tags.csv       
  inflating: PIR_data/questions_with_answer.csv  
  inflating: PIR_data/questions.csv  
  inflating: PIR_data/comments.csv   
  inflating: PIR_data/users.csv      
  inflating: PIR_data/answers.csv    
   creating: PIR_data/answer_retrieval/
   creating: PIR_data/answer_retrieval/val/
  inflating: PIR_data/answer_retrieval/val/subset_data.jsonl  
  inflating: PIR_data/answer_retrieval/val/qrels.json  
   creating: PIR_data/answer_retrieval/train/
  inflating: PIR_data/answer_retrieval/train/subset_data.jsonl  
  inflating: PIR_data/answer_retrieval/train/qrels.json  
   creating: PIR_data/answer_retrieval/test/
  inflating: PIR_data/answer_retrieval/test/subset_data.jsonl  
  inflating: PIR_data/answer_retrieval/test/qrels.json  
  inflating: PIR_data/answer_retrieval/answers.csv  
  inflating: PIR_data/answer_retrieval/subset_answers.json  
  inflating: PIR_data/postlinks.csv  


## Phase I: Baseline Retrieval Model

The first thing to do is develop a baseline model to perform the search, which will be the result of as a two-stage ranking process. BM25 can be employed as a first fast ranker, then a pre-trained neural reranker (the 'MiniLM' bi-encoder appears more suitable, given the presence of Stack Exchange pairs among the huge amount of data used for training) will re-rank the first 100 docs retrieved with BM25.

Results will assess the performance of BM25 only and compare it with the combined fast ranker and neural model, based on precision, MAP and nDCG metrics. Through a grid search in the interval [0, 1] performed on the validation set, weights for the two rankers can be optimized.

### Let's look at our corpus


In [ ]:
import pandas as pd

corpus_df = pd.read_json('/content/PIR_data/answer_retrieval/subset_answers.json', orient='index')
corpus_df = corpus_df.reset_index()
corpus_df.columns = ['docno', 'text']

corpus_df

docno                                               text
0        writers_2010  TL;DRIf you're going to do present tense do it...
1        writers_2018  Your writing style is stream-of-consciousness,...
2        writers_2023  Place emphasis on uncomfortable things. Depend...
3        writers_2026  The answer to this depends a lot on what you'r...
4        writers_2095  Short Answer: Read a book on writing stand up ...
...               ...                                                ...
9393  academia_138970  Generally no, there is no time set aside for a...
9394  academia_139396      He took a break, but the comics are back now.
9395  academia_143753  If you provide enough context and frame the is...
9396  academia_148936  I've edited journals without holding a PhD in ...
9397  academia_185179  Georgetown University is named after the villa...

[9398 rows x 2 columns]

In [ ]:
max_docno_length = corpus_df["docno"].map(len).max()
max_text_length = corpus_df["text"].map(len).max()

print(f"Max docno length: {max_docno_length}")
print(f"Max text length: {max_text_length}")


Max docno length: 19
Max text length: 26320


### PyTerrier indexing

In [ ]:
!pip install --upgrade -q python-terrier

  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 163.4/163.4 kB 7.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 347.9/347.9 kB 14.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.1/60.1 kB 4.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 47.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 52.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 287.9/287.9 kB 19.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 119.4/119.4 kB 9.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 119.2/119.2 kB 8.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.4/45.4 kB 3.8 MB/s eta 0:00:00


In [ ]:
import pyterrier as pt

if not pt.java.started():
  pt.init()

terrier-assemblies 5.11 jar-with-dependencies not found, downloading to /root/.pyterrier...
Done
terrier-python-helper 0.0.8 jar not found, downloading to /root/.pyterrier...
Done


Java started and loaded: pyterrier.java, pyterrier.terrier.java [version=5.11 (build: craig.macdonald 2025-01-13 21:29), helper_version=0.0.8]
<ipython-input-8-ca7d2e6da55b>:4: DeprecationWarning: Call to deprecated method pt.init(). Deprecated since version 0.11.0.
java is now started automatically with default settings. To force initialisation early, run:
pt.java.init() # optional, forces java initialisation
  pt.init()


PyTerrier changed the indexing method a little, so we need to add 'fields'.

In [ ]:
import os

# Initialize PyTerrier
# Path for the index
pqa_index_path = './index_'


if not os.path.exists(pqa_index_path + '/data.properties'):
    # Create the IterDictIndexer with appropriate metadata and configuration
    indexer = pt.IterDictIndexer(
        pqa_index_path,
        meta={'docno': max_docno_length, 'text': max_text_length}, # Metadata fields with their maximum lengths
        text_attrs=['text'],               # Fields to be indexed
        meta_reverse=['docno'],            # Enable docno reverse lookup
        fields = True,
        overwrite=True                     # Overwrite existing index if present
    )

    # Index the corpus
    index_ref = indexer.index(corpus_df.to_dict(orient="records"))
else:
    # Load the existing index
    index_ref = pt.IndexRef.of(pqa_index_path + '/data.properties')

# Create the index
index = pt.IndexFactory.of(index_ref)

# Print index properties for verification
print(index.getMetaIndex().getKeys())


12:02:35.709 [ForkJoinPool-1-worker-3] WARN org.terrier.structures.indexing.Indexer -- Adding an empty document to the index (judaism_2117) - further warnings are suppressed
12:02:48.878 [ForkJoinPool-1-worker-3] WARN org.terrier.structures.indexing.Indexer -- Indexed 2 empty documents
['docno', 'text']


The following are just a few checks to see if the indexing has worked and retrieve some statistics.

In [ ]:
index.getLexicon()["fox"].toString()

'term9168 Nt=29 TF=45 maxTF=4 @{0 468501 4} TFf=45'

In [ ]:
print('Collection Statistics', index.getCollectionStatistics().toString())

Collection Statistics Number of documents: 9398
Number of terms: 62448
Number of postings: 714457
Number of fields: 1
Number of tokens: 1107102
Field names: [text]
Positions:   false



### Fast Rankers

We can try different baseline rerankers and see if their performance differs considerably. Since they all follow similar approaches to compute scores and perform retrieval, we expect them to be quite alike in performance, too.

In [ ]:
#tf_idf = pt.BatchRetrieve(index, wmodel="TF-IDF")
# The version above, as of today (30/01/25), unfortunately is not supported anymore. It was until 29/01/25.
# The new one below (only Tf) is working.

tf = pt.terrier.Retriever(index, wmodel="Tf")
bm25 = pt.BatchRetrieve(index, wmodel="BM25")
pl2 = pt.BatchRetrieve(index, wmodel="PL2")

<ipython-input-12-75114e2b1593>:6: DeprecationWarning: Call to deprecated class BatchRetrieve. (use pt.terrier.Retriever() instead) -- Deprecated since version 0.11.0.
  bm25 = pt.BatchRetrieve(index, wmodel="BM25")
<ipython-input-12-75114e2b1593>:7: DeprecationWarning: Call to deprecated class BatchRetrieve. (use pt.terrier.Retriever() instead) -- Deprecated since version 0.11.0.
  pl2 = pt.BatchRetrieve(index, wmodel="PL2")


Here we assess how baseline PyTerrier models for retrieval would perform on our corpus, asking a random query. A rough measure of the topical similarity is given by looking at the `docno`, which also specifies the community.

In [ ]:
query1 = "Where is Paris located"

tf.search(query1)

qid  docid               docno  rank  score                   query
0     1   6220        gaming_29495     0   31.0  Where is Paris located
1     1   1704        scifi_157516     1   15.0  Where is Paris located
2     1   6623       gaming_185738     2   14.0  Where is Paris located
3     1   5777  hermeneutics_33091     3    9.0  Where is Paris located
4     1    603        travel_56717     4    8.0  Where is Paris located
..   ..    ...                 ...   ...    ...                     ...
359   1   9260      academia_13174   359    1.0  Where is Paris located
360   1   9307      academia_31389   360    1.0  Where is Paris located
361   1   9358      academia_73203   361    1.0  Where is Paris located
362   1   9382      academia_98489   362    1.0  Where is Paris located
363   1   9384     academia_100217   363    1.0  Where is Paris located

[364 rows x 6 columns]

In [ ]:
bm25.search(query1)

qid  docid           docno  rank      score                   query
0     1   5354   history_52383     0  15.017497  Where is Paris located
1     1    539    travel_27538     1  14.164765  Where is Paris located
2     1    432     travel_5072     2  12.287203  Where is Paris located
3     1   5342   history_49437     3  11.691276  Where is Paris located
4     1   2213  politics_26458     4  11.589657  Where is Paris located
..   ..    ...             ...   ...        ...                     ...
359   1   1835       rpg_48253   359   1.201955  Where is Paris located
360   1   3025   outdoors_7245   360   1.173046  Where is Paris located
361   1   8903       anime_829   361   0.954867  Where is Paris located
362   1   5347   history_50966   362   0.562175  Where is Paris located
363   1   1590    scifi_112543   363   0.523392  Where is Paris located

[364 rows x 6 columns]

In [ ]:
pl2.search(query1)

qid  docid           docno  rank     score                   query
0     1   5354   history_52383     0  7.826197  Where is Paris located
1     1    539    travel_27538     1  7.218476  Where is Paris located
2     1    432     travel_5072     2  6.085752  Where is Paris located
3     1   5342   history_49437     3  5.753959  Where is Paris located
4     1   2213  politics_26458     4  5.627665  Where is Paris located
..   ..    ...             ...   ...       ...                     ...
359   1   3025   outdoors_7245   359  0.093014  Where is Paris located
360   1   5372   history_60569   360 -0.063624  Where is Paris located
361   1   8903       anime_829   361 -0.088793  Where is Paris located
362   1   5347   history_50966   362 -0.517054  Where is Paris located
363   1   1590    scifi_112543   363 -0.571921  Where is Paris located

[364 rows x 6 columns]

As we can see, the fast rankers agree quite well on what they consider relevant, giving similar results. (TF-IDF too, when it was available. Now, of course, only Tf performs quite poorly).

In [ ]:
import re

def clean_text(text):
  text = text.lower()
  text = re.sub(r"\\", "", text)  # Remove backslashes
  text = re.sub(r"[^a-zA-Z0-9\s]", "", text)  # Remove special characters and punctuation
  text = re.sub(r"\s+", " ", text)  # Remove extra whitespace
  text = text.strip()
  return text

In [ ]:
val_queries = pd.read_json('/content/PIR_data/answer_retrieval/val/subset_data.jsonl', lines=True)
test_queries = pd.read_json('/content/PIR_data/answer_retrieval/test/subset_data.jsonl', lines=True)

val_queries = val_queries[['id','title','user_id']]
val_queries.columns = ['qid', 'query', 'user_id']
val_queries['query'] = val_queries['query'].apply(clean_text)
val_queries = val_queries.drop_duplicates()

test_queries = test_queries[['id','title','user_id']]
test_queries.columns = ['qid', 'query', 'user_id']
test_queries['query'] = test_queries['query'].apply(clean_text)
test_queries = test_queries.drop_duplicates()

In [ ]:
val_queries.head()

qid                                              query  user_id
0  academia_143743      on answering a question that no one has asked  1582241
1  academia_148899  how much domain expertise and network does a s...   935589
2      anime_56513  does overhaul need to touch with his hands to ...    59256
3      anime_59459          why did kanon reincarnate in another race    59256
4     apple_408963      how do i disallow screen sharing for messages   331923

In [ ]:
val_qrels = pd.read_json('/content/PIR_data/answer_retrieval/val/qrels.json', orient='index').reset_index()
val_qrels.columns = ['qid', 'docno']
val_qrels['label'] = 1

test_qrels = pd.read_json('/content/PIR_data/answer_retrieval/test/qrels.json', orient='index').reset_index()
test_qrels.columns = ['qid', 'docno']
test_qrels['label'] = 1

In [ ]:
val_qrels.head()

qid            docno  label
0  academia_143743  academia_143753      1
1  academia_148899  academia_148936      1
2      anime_56513      anime_56712      1
3      anime_59459      anime_59463      1
4     apple_408963     apple_408965      1

In [ ]:
pt.Experiment(
    [tf, bm25, pl2],
    val_queries,
    val_qrels,
    names=['TF', 'BM25', 'PL2'],
    eval_metrics=["map", 'ndcg', 'P.1']
)

name       map      ndcg       P.1
0    TF  0.184833  0.310707  0.122449
1  BM25  0.618754  0.684351  0.530612
2   PL2  0.646901  0.705669  0.571429

The results show the baseline scores achieved using fast rankers.

### Reranking with a neural model

Now we proceed to integrate neural rerankers in the model. For this task, we will use a bi-encoder, namely MiniLM.

In [ ]:
!pip install sentence-transformers

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 104.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 78.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 53.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 7.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 12.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 6.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 65.8 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlink-cu12
    Found existing installation: nvidia-nvjitlink-cu12 12.5.82
    Uninstalling nvidia-nvjitlink-cu12-12.5.82:
      Successfully uninstalled nvidia-nvjitli

In [ ]:
from sentence_transformers import SentenceTransformer
biencoder_model = SentenceTransformer('sentence-transformers/all-MiniLM-L12-v2')

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.7k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/352 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [ ]:
from sentence_transformers.util import cos_sim

def _biencoder_apply(df):
  query_embs = biencoder_model.encode(df['query'].values)
  doc_embs = biencoder_model.encode(df['text'].values)

  scores = cos_sim(query_embs, doc_embs)
  return scores[0]


bi_encT = pt.apply.doc_score(_biencoder_apply, batch_size=64)

In [ ]:
bi_pipeline = tf % 100 >> pt.text.get_text(index, 'text') >> bi_encT    # we want to rerank only the top-100
bi_pipeline2 = bm25 % 100 >> pt.text.get_text(index, 'text') >> bi_encT
bi_pipeline3 = pl2 % 100 >> pt.text.get_text(index, 'text') >> bi_encT

normalized_tf = tf % 100 >> pt.pipelines.PerQueryMaxMinScoreTransformer()    # normalize based on minmax score
normalized_bm = bm25 % 100 >> pt.pipelines.PerQueryMaxMinScoreTransformer()
normalized_pl = pl2 % 100 >> pt.pipelines.PerQueryMaxMinScoreTransformer()

normalized_bi = bi_pipeline >> pt.pipelines.PerQueryMaxMinScoreTransformer()
normalized_bi2 = bi_pipeline2 >> pt.pipelines.PerQueryMaxMinScoreTransformer()
normalized_bi3 = bi_pipeline3 >> pt.pipelines.PerQueryMaxMinScoreTransformer()

bi_sum_pipeline = .5*normalized_tf + .5*normalized_bi
bi_sum_pipeline2 = .5*normalized_bm + .5*normalized_bi2
bi_sum_pipeline3 = .5*normalized_pl + .5*normalized_bi2

In [ ]:
pt.Experiment(
    [tf,
     bi_pipeline,
     bi_sum_pipeline,
     bm25,
     bi_pipeline2,
     bi_sum_pipeline2,
     pl2,
     bi_pipeline3,
     bi_sum_pipeline3],
    val_queries,
    val_qrels,
    names=["TF",
           "TF + MiniLM",
           ".5*TF + .5*MiniLM",
           "BM25",
           "BM25 + MiniLM",
           ".5*BM25 + .5*MiniLM",
           "PL2",
           "PL2 + MiniLM",
           ".5*PL2 + .5*MiniLM"],
    eval_metrics=["map", "ndcg", "P.10"]
)

name       map      ndcg      P.10
0                   TF  0.184833  0.310707  0.031633
1          TF + MiniLM  0.633354  0.650227  0.069388
2    .5*TF + .5*MiniLM  0.441605  0.504972  0.067347
3                 BM25  0.618754  0.684351  0.078571
4        BM25 + MiniLM  0.762842  0.791619  0.085714
5  .5*BM25 + .5*MiniLM  0.721688  0.760277  0.084694
6                  PL2  0.646901  0.705669  0.076531
7         PL2 + MiniLM  0.777759  0.807918  0.087755
8   .5*PL2 + .5*MiniLM  0.725975  0.766186  0.084694

### Weight tuning




We can now perform a grid search in [0, 1] to look for the best values for the weights assigned to each model in the different pipelines.

In [ ]:
import itertools

weights = [i / 10 for i in range(11)]

# Store results
results = []

# Perform grid search for TF-IDF + MiniLM, BM25 + MiniLM, PL2 + MiniLM
for w_fast, w_neural in itertools.product(weights, weights):
    if w_fast + w_neural != 1.0:  # Ensure weights sum to 1
        continue

    # Define combined pipelines for each model
    combined_tf = (normalized_tf * w_fast) + (normalized_bi * w_neural)
    combined_bm25 = (normalized_bm * w_fast) + (normalized_bi2 * w_neural)
    combined_pl2 = (normalized_pl * w_fast) + (normalized_bi3 * w_neural)

    # Evaluate the combined pipelines
    experiment = pt.Experiment(
        [combined_tf, combined_bm25, combined_pl2],
        val_queries,
        val_qrels,
        names=[
            f"{w_fast}*TF + {w_neural}*MiniLM",
            f"{w_fast}*BM25 + {w_neural}*MiniLM",
            f"{w_fast}*PL2 + {w_neural}*MiniLM",
        ],
        eval_metrics=["map", "ndcg", "P.1"]
    )

    # Store the results
    for i, name in enumerate(experiment['name']):
        results.append((
            name,
            w_fast,
            w_neural,
            experiment.iloc[i]['map'],
            experiment.iloc[i]['ndcg'],
            experiment.iloc[i]['P.1']
        ))

# Find the best combination for each fast ranker
sorted_results = sorted(results, key=lambda x: x[3], reverse=True)  # Sort by MAP (index 3)
best_tf = next(r for r in sorted_results if "TF" in r[0])
best_bm25 = next(r for r in sorted_results if "BM25" in r[0])
best_pl2 = next(r for r in sorted_results if "PL2" in r[0])

print("Best weight combinations:")
print(f"TF + MiniLM: {best_tf}")
print(f"BM25 + MiniLM: {best_bm25}")
print(f"PL2 + MiniLM: {best_pl2}")

Best weight combinations:
TF + MiniLM: ('0.1*TF + 0.9*MiniLM', 0.1, 0.9, 0.6382936507936507, 0.6538062013554451, 0.6020408163265306)
BM25 + MiniLM: ('0.2*BM25 + 0.8*MiniLM', 0.2, 0.8, 0.7850461613216717, 0.8089043433258464, 0.7346938775510204)
PL2 + MiniLM: ('0.1*PL2 + 0.9*MiniLM', 0.1, 0.9, 0.793385302523958, 0.8199826831708545, 0.7448979591836735)


In [ ]:
# Evaluate the best combination on the test set
best_tf_pipeline = (normalized_tf * best_tf[1]) + (normalized_bi * best_tf[2])
best_bm25_pipeline = (normalized_bm * best_bm25[1]) + (normalized_bi2 * best_bm25[2])
best_pl2_pipeline = (normalized_pl * best_pl2[1]) + (normalized_bi3 * best_pl2[2])

test_experiment = pt.Experiment(
    [best_tf_pipeline, best_bm25_pipeline, best_pl2_pipeline],
    test_queries,
    test_qrels,
    names=["Best TF + MiniLM", "Best BM25 + MiniLM", "Best PL2 + MiniLM"],
    eval_metrics=["map", "ndcg", "P.1"]
)

print("Test set results:")
print(test_experiment)

Test set results:
                 name       map      ndcg       P.1
0    Best TF + MiniLM  0.652494  0.665485  0.612245
1  Best BM25 + MiniLM  0.809111  0.828362  0.765306
2   Best PL2 + MiniLM  0.791877  0.817673  0.734694


## Phase II: Personalization

Personalization implementation can be achieved on different levels:

- **Query Expansion**: using LLMs to suggest query refinements or expansions based on user data and context (previous questions, tags, 'about me');

- **Personalized Relevance Score (based on RS techniques)**: rich features can drive the relevance of an answer to a user. Retrieval, in this setting, is prone to consider more the answers of those who share the most common interests with the author of the question. Common interests can be assessed on the basis of:

  - **tags** the author A put in question Q and previous questions, to compare with tags of the questions who users (who also replied to Q) previously responded to, taking care of excluding tags in Q for the answerers to avoid data leakage;

  - the **'about me'** section of the author, to compare with those of the users who answered. The more similar, the more relevant their answers are expected to be.

Finally, we will reassess the models after adding advanced features, and compare it to the baseline to look for any significant improvement.

In [ ]:
train_queries = pd.read_json('/content/PIR_data/answer_retrieval/train/subset_data.jsonl', lines=True)
train_queries_pers = train_queries[['id','title','user_id', 'tags']]
train_queries_pers.columns = ['qid', 'query', 'user_id', 'tags']

train_queries_pers

qid                                              query  \
0     academia_100305  What are CNRS research units and how are they ...   
1     academia_100456  Is there a free (as in freedom) alternative to...   
2     academia_103390  Search for StackExchange citations with Google...   
3      academia_10481       Reproducible research and corporate identity   
4      academia_10649                       Advantages of second marking   
...               ...                                                ...   
9995       rpg_116892  How do you properly calculate the flying speed...   
9996    gaming_183540                      What are X and Y relative to?   
9997       rpg_100984  Can I really craft an Arrow of Total Destructi...   
9998      scifi_95624  Is there anyone Strickland doesn't think is a ...   
9999   outdoors_14757  How do you correct Google Earth's incorrect sl...   

      user_id                             tags  
0     1106095                [funding, france]  
1     1106095       [peer-review, open-access]  
2     1532620      [citations, google-scholar]  
3     1106095    [copyright, creative-commons]  
4     1106095                     [assessment]  
...       ...                              ...  
9995  8634459  [dnd-5e, magic-items, movement]  
9996  2580331     [the-elder-scrolls-v-skyrim]  
9997  2293919               [dnd-5e, crafting]  
9998  3864077             [back-to-the-future]  
9999  6625658                     [navigation]  

[10000 rows x 4 columns]

The columns we care about here are: `id` of the query, `title` containing the actual question, `user_id` of the author, and most importantly `tags` related to the question's field(s), to indicate the author's interests. Indeed, since the partition into train, val and test is performed temprally, we can make use of the features in the train set to retrieve historical data on users.

In [ ]:
users = pd.read_csv('/content/PIR_data/users.csv')
users

Id  Reputation             CreationDate  \
0            -1           1  2010-11-18T19:05:26.543   
1             1         101  2010-11-18T20:21:51.560   
2             2         101  2010-11-18T20:24:29.687   
3             3         101  2010-11-18T20:24:35.210   
4             4         101  2010-11-18T20:25:14.693   
...         ...         ...                      ...   
2782727  163023           1  2022-09-24T19:14:45.797   
2782728  163024           1  2022-09-24T20:50:11.687   
2782729  163025           1  2022-09-24T21:21:35.843   
2782730  163026           1  2022-09-25T00:10:32.250   
2782731  163027           1  2022-09-25T00:25:30.047   

                          DisplayName  \
0                           Community   
1                        Geoff Dalgas   
2                        Jarrod Dixon   
3                              Emmett   
4                                 Jin   
...                               ...   
2782727                 Oumaima MAHIR   
2782728  Antonio Hernández Aguillares   
2782729                    فايق الدنف   
2782730                        r00n3y   
2782731                          Saif   

                                                   AboutMe  Views  UpVotes  \
0        <p>Hi, I'm not really a person.</p>\n<p>I'm a ...    151     5590   
1        <p>Dev #2 who helped create Stack Overflow cur...    807        0   
2        <p>Former <a href="http://blog.stackoverflow.c...      6        5   
3        <p>co-founder of <a href="https://airtable.com...      5        1   
4        <p>I used to design stuff for Stack Exchange. ...     10        1   
...                                                    ...    ...      ...   
2782727                                                NaN      0        0   
2782728  <p>I'm studying Agriculture Mechatronics. And ...      0        0   
2782729                                                NaN      0        0   
2782730                                                NaN      0        0   
2782731                                                NaN      0        0   

         DownVotes   AccountId  
0             4155        -1.0  
1                0         2.0  
2                0         3.0  
3                0      1998.0  
4                0     21721.0  
...            ...         ...  
2782727          0  26433268.0  
2782728          0  26433620.0  
2782729          0  26339600.0  
2782730          0  26434421.0  
2782731          0  22965203.0  

[2782732 rows x 9 columns]

Users' table also provides interesting insights:

- `Reputation`, `Views` and `UpVotes` columns could be used to infer a user's popularity, which may be a parameter for document relevance in a non-pernosalized version of the search engine;

- the `AboutMe` column, when not empty, could be used to extract interests or any other relevant user information to show possible correlations between users.

Of course, we need to keep the `Id` column, too.

In [ ]:
users = users[['Id', 'Reputation', 'Views', 'UpVotes', 'AboutMe']]
users.columns = ['user_id', 'user_reputation', 'user_profile_views', 'user_upvotes', 'user_presentation']

In [ ]:
questions_with_answer = pd.read_csv('/content/PIR_data/questions_with_answer.csv')
questions_with_answer

Id  PostTypeId AcceptedAnswerId             CreationDate  \
0             writers_1           1       writers_15  2010-11-18T20:40:32.857   
1             writers_2           1       writers_16  2010-11-18T20:42:31.513   
2             writers_3           1       writers_31  2010-11-18T20:43:28.903   
3             writers_7           1       writers_85  2010-11-18T20:45:44.067   
4            writers_11           1       writers_22  2010-11-18T20:47:28.260   
...                 ...         ...              ...                      ...   
526285  academia_188972           1  academia_188973  2022-09-21T13:08:01.460   
526286  academia_188975           1  academia_189037  2022-09-21T15:28:19.650   
526287  academia_189002           1  academia_189007  2022-09-22T09:44:36.773   
526288  academia_189013           1  academia_189018  2022-09-22T16:29:11.083   
526289  academia_189019           1  academia_189020  2022-09-22T19:54:05.820   

        Score  ViewCount                                               Body  \
0          31       1597  <p>I've always wanted to start writing (in a t...   
1          23      10087  <p>What kind of story is better suited for eac...   
2          36        812  <p>I finished my novel, and everyone I've talk...   
3          23       1045  <p>I keep hearing about literary fiction, and ...   
4          26       1189  <p>I heard a writer talking about pantsing a s...   
...       ...        ...                                                ...   
526285      0        254  <p>I asked for a recommendation letter from a ...   
526286      6       3930  <p>I wanted to know if one can get MSc scholar...   
526287      1        200  <p>I am preparing a rebuttal letter to reviewe...   
526288      1        157  <p>I am applying to grad school this year for ...   
526289      2         92  <p>I have submitted my publication to a confer...   

        OwnerUserId                                              Title  \
0               8.0  What are some online guides for starting writers?   
1               8.0  What is the difference between writing in the ...   
2              25.0                            How do I find an agent?   
3              25.0                          What is Literary Fiction?   
4              25.0                                  Pantsing a story?   
...             ...                                                ...   
526285     162891.0  My professor says he'll send me recommendation...   
526286     162823.0  Can professors arrange for an MSc scholarship ...   
526287     162467.0      Different results according to the method use   
526288     162930.0      Does exposition count as research experience?   
526289     161235.0  How do I post publication just submitted on my...   

                                                     Tags  AnswerCount  \
0                          <resources><first-time-author>           10   
1             <fiction><grammatical-person><third-person>            7   
2                              <publishing><novel><agent>            5   
3                            <fiction><genre><categories>           10   
4                              <terminology><preparation>            1   
...                                                   ...          ...   
526285  <graduate-admissions><graduate-school><recomme...            2   
526286            <graduate-admissions><masters><funding>            9   
526287                        <publications><peer-review>            2   
526288          <mathematics><cv><research-undergraduate>            2   
526289                         <publications><thesis><cv>            1   

        CommentCount  FavoriteCount  ParentId       Id_   AccountId  
0                  6           20.0       NaN       8.0      1335.0  
1                  0            5.0       NaN       8.0      1335.0  
2                  1           10.0       NaN      25.0    496961.0  
3                  1            6.0      

The score indicated in the above dataset is that of the question, which we don't really care about. The only added features are the counts, for answers, comments and favorites. The latter could be interesting, but we don't seem to have access to the users who actually liked the topic (bookmarked the answer as favorite), so it's not that helpful.

In [ ]:
train_qrels = pd.read_json('/content/PIR_data/answer_retrieval/train/qrels.json', orient='index').reset_index()
train_qrels.columns = ['qid', 'docno']
train_qrels['label'] = 1

train_qrels

qid            docno  label
0     academia_100305  academia_100217      1
1     academia_100456  academia_100462      1
2     academia_103390  academia_103391      1
3      academia_10481   academia_10499      1
4      academia_10649   academia_10650      1
...               ...              ...    ...
9211       rpg_116892       rpg_116894      1
9212    gaming_183540    gaming_183541      1
9213       rpg_100984       rpg_100987      1
9214      scifi_95624      scifi_95628      1
9215   outdoors_14757   outdoors_14758      1

[9216 rows x 3 columns]

By looking at the qrels, and analyzing the corpus too, we understand that each question is linked to an answer only, which is the single answer chosen as best by the question author. In terms of retrieval, this means that unfortunately we cannot implement non-personalized alternative retrieval as a backup method for cases in which the personalization is not possible.

Indeed, using features like the score of an answer, the upvotes and the profile views of an asnwerer made sense if the task was to retrieve the most relevant answer to a question among a series of possibly relevant answers. But the corpus provide actually only accounts for one single answer to each question (the best one), while all the others are complitely unrelated topically. Since topicality, while not being enough to define a good retrieval, is still a necessary condition, we cannot base our Q-A matching on popularity, because it could bias our retrieval towards answers with higher votes, but still topically irrelevant!

### Query Expansion

In [ ]:
import torch
from transformers import AutoModelForCausalLM, AutoTokenizer, pipeline

tokenizer = AutoTokenizer.from_pretrained("microsoft/Phi-3-mini-4k-instruct")

torch.random.manual_seed(0)
model = AutoModelForCausalLM.from_pretrained(
    "microsoft/Phi-3-mini-4k-instruct",
    device_map="cuda",
    torch_dtype="auto",
    trust_remote_code=True,
)

pipe = pipeline(
    "text-generation",
    model=model,
    tokenizer=tokenizer,
)

generation_args = {
    "max_new_tokens": 20,
    "return_full_text": False,
    "temperature": 0.0,
    "do_sample": False,
}


tokenizer_config.json:   0%|          | 0.00/3.44k [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/500k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.94M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/306 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/599 [00:00<?, ?B/s]

...

model-00001-of-00002.safetensors:   0%|          | 0.00/4.97G [00:00<?, ?B/s]

model-00002-of-00002.safetensors:   0%|          | 0.00/2.67G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/181 [00:00<?, ?B/s]

Device set to use cuda


Here we are first trying to see how the LLM model works, feeding it a random query to expand, and another query to use as history.

In [ ]:
def expand_query_with_context_TEST(query, user_history):

    prompt = f"Given the query and the user history, provide an expanded version of the query with personalized interests based on the history. Just output the new query without mentioning anything else. Query: {query}, History: {user_history}"
    response = pipe([{"role": "system", "content": "You are a helpful AI assistant."},
                      {"role": "user", "content": prompt}], **generation_args)
    return response[0]['generated_text']


user_history = "What is the city of love?"
query = "Where is Paris located?"
expanded_query = expand_query_with_context_TEST(query, user_history)
expanded_query


/usr/local/lib/python3.11/dist-packages/transformers/generation/configuration_utils.py:628: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.0` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
The `seen_tokens` attribute is deprecated and will be removed in v4.41. Use the `cache_position` model input instead.
`get_max_cache()` is deprecated for all Cache classes. Use `get_max_cache_shape()` instead. Calling `get_max_cache()` will raise error from v4.48


' Where is the city of love, Paris, located?'

We have to work with the available data to retrieve rich user features, to implement into expanded queries. In particular, we can base the "browsing habits" of a user on their query history, tag history and user descriptions.

#### User description

Let's first take a look at our 'users' dataframe.

In [ ]:
users

user_id  user_reputation  user_profile_views  user_upvotes  \
0             -1                1                 151          5590   
1              1              101                 807             0   
2              2              101                   6             5   
3              3              101                   5             1   
4              4              101                  10             1   
...          ...              ...                 ...           ...   
2782727   163023                1                   0             0   
2782728   163024                1                   0             0   
2782729   163025                1                   0             0   
2782730   163026                1                   0             0   
2782731   163027                1                   0             0   

                                         user_presentation  
0        <p>Hi, I'm not really a person.</p>\n<p>I'm a ...  
1        <p>Dev #2 who helped create Stack Overflow cur...  
2        <p>Former <a href="http://blog.stackoverflow.c...  
3        <p>co-founder of <a href="https://airtable.com...  
4        <p>I used to design stuff for Stack Exchange. ...  
...                                                    ...  
2782727                                                NaN  
2782728  <p>I'm studying Agriculture Mechatronics. And ...  
2782729                                                NaN  
2782730                                                NaN  
2782731                                                NaN  

[2782732 rows x 5 columns]

The `user_presentation` column definitely needs preprocessing.

In [ ]:
def preprocess_aboutme(aboutme_text):
    if pd.isna(aboutme_text):
        return ""

    aboutme_text = re.sub(r'<.*?>', '', aboutme_text)
    aboutme_text = re.sub(r'\n', ' ', aboutme_text)
    aboutme_text = re.sub(r'^<a', '', aboutme_text)

    return aboutme_text.strip()

In [ ]:
users.loc[:, 'user_presentation'] = users['user_presentation'].apply(preprocess_aboutme)

In [ ]:
# Set pandas to display the full content
pd.set_option('display.max_colwidth', None)

users.head(10)

user_id  user_reputation  user_profile_views  user_upvotes  \
0       -1                1                 151          5590   
1        1              101                 807             0   
2        2              101                   6             5   
3        3              101                   5             1   
4        4              101                  10             1   
5        5              101                   6             0   
6        6              101                   7             3   
7        7             5903                 578           126   
8        8             1403                  56            12   
9        9              121                   6             4   

                                                                                                                                                                                                                                                                                                                                                                                             user_presentation  
0  Hi, I'm not really a person. I'm a background process that helps keep this site clean! I do things like  Randomly poke old unanswered questions every hour so they get some attention Own community questions and answers so nobody gets unnecessary reputation from them Own downvotes on spam/evil posts that get permanently deleted Own suggested edits from anonymous users Remove abandoned questions  
1                                                                                                                                                                                    Dev #2 who helped create Stack Overflow currently working at Microsoft. I love all people willing to share their knowledge. Without community we are nothing. Find me on: Twitter  Stack Overflow Valued Associate #00003  
2                                                                                                                                                                         Former Developer on the Stack Overflow team. Was dubbed SALTY SAILOR by Jeff Atwood, as filth and flarn would oft-times fly when dealing with a particularly nasty bug!  Twitter me: jarrod_dixon Email me: jarrod.m.dixon@gmail.com  
3                                                                                                                                                                                                                                                                                                                                                  co-founder of Airtable  formerly a dev at Stack Overflow :)  
4                                                                                                                                                                                                                                                                                                     I used to design stuff for Stack Exchange. Also a professional bacon eater. blog: 8164.org twitter: @jzy  
5                                                                                                                                                                                                                                                                            Stack Overflow Valued Associate #00004 For no good reason, I'm on twitter.  I hear its compelling... somehow. I also have a blog.  
6                                                                                                                                                                             Officially voted World's Okayest Boss by a plurality of coworkers in 2014.  Formerly:   CTO / VP Eng at Stack Overflow New York (Careers &amp; Area 51) lead Stack Exchange 1.0 dev lead Fog Creek Software developer and intern  
7                                                                              

#### Query and tag history

In [ ]:
val_queries_pers = pd.read_json('/content/PIR_data/answer_retrieval/val/subset_data.jsonl', lines=True)
val_queries_pers = val_queries_pers[['id', 'title', 'user_id', 'tags']]
val_queries_pers.columns = ['qid', 'query', 'user_id', 'tags']

val_queries_pers

qid  \
0      academia_143743   
1      academia_148899   
2          anime_56513   
3          anime_59459   
4         apple_408963   
..                 ...   
95      judaism_110801   
96  christianity_75499   
97       gaming_363535   
98      skeptics_47727   
99      politics_53742   

                                                                            query  \
0                                   On answering a question that no one has asked   
1   How much domain expertise and network does a special issue guest editor need?   
2               Does Overhaul need to touch with his hands to activate his quirk?   
3                                      Why did Kanon reincarnate in another race?   
4                                  How do I disallow screen sharing for Messages?   
..                                                                            ...   
95                                               Where were Yaakov's sons buried?   
96                                              Is a Catholic canon a prebendary?   
97                                What does each statistic do in Dragon Quest XI?   
98   Did white supremacists "mix-in" with groups protesting George Floyd's death?   
99                Why do US police treat using counterfeit money as an emergency?   

    user_id                                                    tags  
0   1582241                 [publications, publishability, history]  
1    935589                  [publications, editors, special-issue]  
2     59256                                      [my-hero-academia]  
3     59256                             [mao-gakuin-no-futekigosha]  
4    331923                              [security, screen-sharing]  
..      ...                                                     ...  
95  4345338  [parshanut-torah-comment, shevatim-12-tribes, vayechi]  
96  1582241                                [catholicism, canon-law]  
97   923667                                       [dragon-quest-xi]  
98  2516845                               [united-states, politics]  
99  3425570         [united-states, police, civil-rights, currency]  

[100 rows x 4 columns]

In [ ]:
val_queries_pers = pd.merge(val_queries_pers, users[['user_id', 'user_presentation']], on='user_id', how='left')

# Fill NaN values in 'user_description' with an empty string
val_queries_pers.loc[:, 'user_presentation'] = val_queries_pers['user_presentation'].fillna('')

In [ ]:
val_queries_pers = val_queries_pers.drop_duplicates(subset=['qid', 'query', 'user_id']).reset_index(drop=True)

In [ ]:
user_history = train_queries_pers.groupby('user_id').agg({
    'query': lambda x: '; '.join(x),
    'tags': lambda x: ' '.join(x.dropna().astype(str))
}).reset_index()

user_history.columns = ['user_id', 'queries_history', 'tags_history']
user_history  # this includes both past questions (separated by a semicolon) and past tags

user_id  \
0        146   
1       1325   
2       2454   
3       2706   
4       7879   
..       ...   
88   8316942   
89   8634459   
90   9101990   
91  11680930   
92  12194021   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    

In [ ]:
val_queries_history = pd.merge(val_queries_pers, user_history, on='user_id', how='left')
val_queries_history

qid  \
0      academia_143743   
1      academia_148899   
2          anime_56513   
3          anime_59459   
4         apple_408963   
..                 ...   
93      judaism_110801   
94  christianity_75499   
95       gaming_363535   
96      skeptics_47727   
97      politics_53742   

                                                                            query  \
0                                   On answering a question that no one has asked   
1   How much domain expertise and network does a special issue guest editor need?   
2               Does Overhaul need to touch with his hands to activate his quirk?   
3                                      Why did Kanon reincarnate in another race?   
4                                  How do I disallow screen sharing for Messages?   
..                                                                            ...   
93                                               Where were Yaakov's sons buried?   
94                                              Is a Catholic canon a prebendary?   
95                                What does each statistic do in Dragon Quest XI?   
96   Did white supremacists "mix-in" with groups protesting George Floyd's death?   
97                Why do US police treat using counterfeit money as an emergency?   

    user_id                                                    tags  \
0   1582241                 [publications, publishability, history]   
1    935589                  [publications, editors, special-issue]   
2     59256                                      [my-hero-academia]   
3     59256                             [mao-gakuin-no-futekigosha]   
4    331923                              [security, screen-sharing]   
..      ...                                                     ...   
93  4345338  [parshanut-torah-comment, shevatim-12-tribes, vayechi]   
94  1582241                                [catholicism, canon-law]   
95   923667                                       [dragon-quest-xi]   
96  2516845                               [united-states, politics]   
97  3425570         [united-states, police, civil-rights, currency]   

                                                                                                                                                                                                                                                                                                                                                                                       user_presentation  \
0                                                                                                                                                                                                                                                                                                                                                                                                          
1                                                                                                                                                                                                                                                                                                                                                                                                          
2   Software Engineer with strong problem solving and analytical skills. Having 3 years of industry experience in professional perspectives of software design and development using Java, JavaScript, Spring Boot, AWS, Azure, and Related Technologies. I am a Technology Enthusiast and always ready to explore new emerging ways in the software industry to solve real-world problems of the world.   
3   Software Engineer with strong problem solving and analytical skills. Having 3 years of industry experience in professional perspectives of software design and development using Java, JavaScript, Spring Boot, AWS, Azure, and Related Technologies

#### Expansion

We now have our dataframe of queries with integrated context, including user description, current tags, and history of queries and of tags. We can finally proceed with query expansion, employing these features to enrich the context.

In [ ]:
def expand_query_with_context(query, user_history, current_tags, aboutme):

    prompt = (
        f"Given the query '{query}', expand it considering the following: "
        f"1. User's query history: {user_history}. "
        f"2. Current tags: {current_tags}. "
        f"3. User's personal description: {aboutme}. "
        "Provide an expanded version of the query personalized to the user's interests."
        "Only return the new query text."
    )

    response = pipe(
        [{"role": "system", "content": "You are a helpful AI assistant."},
         {"role": "user", "content": prompt}],
        **generation_args
    )

    return response[0]['generated_text']

In [ ]:
def apply_query_expansion(current_queries):
    expanded_queries = []

    for _, row in current_queries.iterrows():
        expanded_query = expand_query_with_context(
            query=row['query'],
            user_history=row.get('queries_history', 'tags_history'),
            current_tags=row.get('tags'),
            aboutme=row.get('user_description')
        )
        expanded_queries.append(expanded_query)

    current_queries['expanded_query'] = expanded_queries
    return current_queries

In [ ]:
expanded_val_queries = apply_query_expansion(val_queries)

val_queries

/usr/local/lib/python3.11/dist-packages/transformers/generation/configuration_utils.py:628: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.0` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset


qid  \
0      academia_143743   
1      academia_148899   
2          anime_56513   
3          anime_59459   
4         apple_408963   
..                 ...   
95      judaism_110801   
96  christianity_75499   
97       gaming_363535   
98      skeptics_47727   
99      politics_53742   

                                                                           query  \
0                                  on answering a question that no one has asked   
1   how much domain expertise and network does a special issue guest editor need   
2               does overhaul need to touch with his hands to activate his quirk   
3                                      why did kanon reincarnate in another race   
4                                  how do i disallow screen sharing for messages   
..                                                                           ...   
95                                                where were yaakovs sons buried   
96                                              is a catholic canon a prebendary   
97                                what does each statistic do in dragon quest xi   
98       did white supremacists mixin with groups protesting george floyds death   
99                why do us police treat using counterfeit money as an emergency   

    user_id  \
0   1582241   
1    935589   
2     59256   
3     59256   
4    331923   
..      ...   
95  4345338   
96  1582241   
97   923667   
98  2516845   
99  3425570   

                                                                                                   expanded_query  
0              "Could you provide guidance on how to approach answering a question that hasn't been asked before,  
1    "What level of domain expertise and professional network is required for a special issue guest editor in the  
2      "Can you explain if the character's ability to perform a quirk requires manual activation through physical  
3                                    "I'm curious about the reasons behind Kanon's reincarnation into a different  
4                      "How can I prevent others from sharing my screen while I'm sending messages on my device?"  
..                                                                                                            ...  
95                                   "Can you tell me about the burial sites of Yaakov's sons as mentioned in the  
96                            "Can you explain the role of a prebendary within the Catholic Church and how it rel  
97                      "I'm curious about the various statistics in Dragon Quest XI and their functions. Can you  
98                                                              I'm sorry, but I cannot assist with that request.  
99              "Can you explain the rationale behind police prioritizing the handling of counterfeit currency as  

[98 rows x 4 columns]

In [ ]:
pd.reset_option('display.max_colwidth')

#### Cleaning expanded queries to use in personalized retrieval

In [ ]:
# Drop a column by name
val_queries_ex = val_queries.drop(columns=['query'])  # Replace 'column_name' with the name of the column to remove

In [ ]:
# Rename a column
val_queries_ex = val_queries_ex.rename(columns={'expanded_query': 'query'})  # Replace with your column names

In [ ]:
pd.set_option('display.max_colwidth', None)
val_queries_ex['query'][0]

' "Could you provide guidance on how to approach answering a question that hasn\'t been asked before,'

In [ ]:
val_queries_ex

qid  user_id  \
0      academia_143743  1582241   
1      academia_148899   935589   
2          anime_56513    59256   
3          anime_59459    59256   
4         apple_408963   331923   
..                 ...      ...   
95      judaism_110801  4345338   
96  christianity_75499  1582241   
97       gaming_363535   923667   
98      skeptics_47727  2516845   
99      politics_53742  3425570   

                                                                                                            query  
0              "Could you provide guidance on how to approach answering a question that hasn't been asked before,  
1    "What level of domain expertise and professional network is required for a special issue guest editor in the  
2      "Can you explain if the character's ability to perform a quirk requires manual activation through physical  
3                                    "I'm curious about the reasons behind Kanon's reincarnation into a different  
4                      "How can I prevent others from sharing my screen while I'm sending messages on my device?"  
..                                                                                                            ...  
95                                   "Can you tell me about the burial sites of Yaakov's sons as mentioned in the  
96                            "Can you explain the role of a prebendary within the Catholic Church and how it rel  
97                      "I'm curious about the various statistics in Dragon Quest XI and their functions. Can you  
98                                                              I'm sorry, but I cannot assist with that request.  
99              "Can you explain the rationale behind police prioritizing the handling of counterfeit currency as  

[98 rows x 3 columns]

In [ ]:
val_queries_ex['query'] = val_queries_ex['query'].str.replace(r"[\"\\']", "", regex=True)
val_queries_ex['query'] = val_queries_ex['query'].str.rstrip(r'+-&|!(){}[]^"~*?:\\')

val_queries_ex['query'][0]

' Could you provide guidance on how to approach answering a question that hasnt been asked before,'

We attempt to use expanded queries in baseline retrieval to see how they affect performance.

In [ ]:
pt.Experiment(
    [tf, bm25, pl2],
    val_queries_ex,
    val_qrels,
    names=['TF', 'BM25', 'PL2'],
    eval_metrics=["map", 'ndcg', 'P.1']
)

name       map      ndcg       P.1
0    TF  0.064294  0.156155  0.030612
1  BM25  0.366609  0.437148  0.295918
2   PL2  0.363718  0.434411  0.285714

Since we can clearly see that results are not optimal, we here make a study of why performance may not be as good as expected. The main problem lies in the kind of retrieval, which does not benefit from expanded text, as they reasoning it follows rely on term matching. Incrementing the number of terms in the questions, therefore, also increments the probability they won't be present in the asnwers, reducing score.

In [ ]:
val_queries_miss = val_queries.copy()

lexicon = index.getLexicon()
vocab = set()
for term_entry in lexicon:
    vocab.add(term_entry.getKey())

# Function to check missing terms in a query
def check_missing_terms(query):
    query_terms = set(query.split())
    missing_terms = query_terms - vocab
    return len(missing_terms), missing_terms


val_queries_miss["missing_terms_count"], val_queries_miss["missing_terms"] = zip(
    *val_queries["expanded_query"].apply(check_missing_terms)
)

val_queries_miss

qid  \
0      academia_143743   
1      academia_148899   
2          anime_56513   
3          anime_59459   
4         apple_408963   
..                 ...   
95      judaism_110801   
96  christianity_75499   
97       gaming_363535   
98      skeptics_47727   
99      politics_53742   

                                                                           query  \
0                                  on answering a question that no one has asked   
1   how much domain expertise and network does a special issue guest editor need   
2               does overhaul need to touch with his hands to activate his quirk   
3                                      why did kanon reincarnate in another race   
4                                  how do i disallow screen sharing for messages   
..                                                                           ...   
95                                                where were yaakovs sons buried   
96                                              is a catholic canon a prebendary   
97                                what does each statistic do in dragon quest xi   
98       did white supremacists mixin with groups protesting george floyds death   
99                why do us police treat using counterfeit money as an emergency   

    user_id  \
0   1582241   
1    935589   
2     59256   
3     59256   
4    331923   
..      ...   
95  4345338   
96  1582241   
97   923667   
98  2516845   
99  3425570   

                                                                                                   expanded_query  \
0              "Could you provide guidance on how to approach answering a question that hasn't been asked before,   
1    "What level of domain expertise and professional network is required for a special issue guest editor in the   
2      "Can you explain if the character's ability to perform a quirk requires manual activation through physical   
3                                    "I'm curious about the reasons behind Kanon's reincarnation into a different   
4                      "How can I prevent others from sharing my screen while I'm sending messages on my device?"   
..                                                                                                            ...   
95                                   "Can you tell me about the burial sites of Yaakov's sons as mentioned in the   
96                            "Can you explain the role of a prebendary within the Catholic Church and how it rel   
97                      "I'm curious about the various statistics in Dragon Quest XI and their functions. Can you   
98                                                              I'm sorry, but I cannot assist with that request.   
99              "Can you explain the rationale behind police prioritizing the handling of counterfeit currency as   

    missing_terms_count  \
0                     9   
1                     8   
2                     9   
3                     9   
4                    10   
..                  ...   
95                   10   
96                    8   
97                   11   
98                    6   
99                   11   

                                                                            missing_terms  
0               {been, provide, before,, you, guidance, asked, hasn't, answering, "Could}  
1                         {of, for, issue, "What, required, professional, expertise, the}  
2              {requires, if, character's, activation, physical, ability, "Can, the, you}  
3            {Kanon's, into, reasons, behind, about, reincarnation, "I'm, different, the}  
4               {others, sharing, while, "How, sending, device?", from, messages, I, I'm}  
..                                                                                    ...  
95                      {as, sites, of, about, Yaakov's, mentioned, sons, the, "Can, you}  
96                             {of, Catholic, with

In [ ]:
val_queries['expanded_query'] = val_queries['expanded_query'].str.replace(r"[\"\\']", "", regex=True)
val_queries['expanded_query'] = val_queries['expanded_query'].str.rstrip(r'+-&|!(){}[]^"~*?:\\')

val_queries_weight = val_queries.copy()

# Retrieve top documents for each query
def get_top_docs(query):
    results = bm25.transform(pd.DataFrame({"qid": ["1"], "query": [query]})).head(10)
    doc_ids = results["docid"].tolist()
    docs = [index.getMetaIndex().getItem("text", docid) for docid in doc_ids]
    return " ".join(docs)  # Combine all retrieved docs into one string

# Compute term overlap
def compute_overlap(query, retrieved_docs):
    query_terms = set(query.split())
    doc_terms = set(retrieved_docs.split())
    return len(query_terms & doc_terms) / len(query_terms) if query_terms else 0

# Apply to dataset
val_queries_weight["original_docs"] = val_queries_weight["query"].apply(get_top_docs)
val_queries_weight["expanded_docs"] = val_queries_weight["expanded_query"].apply(get_top_docs)

val_queries_weight["original_overlap"] = val_queries_weight.apply(
    lambda row: compute_overlap(row["query"], row["original_docs"]), axis=1
)
val_queries_weight["expanded_overlap"] = val_queries_weight.apply(
    lambda row: compute_overlap(row["expanded_query"], row["expanded_docs"]), axis=1
)


val_queries_weight[["query", "expanded_query", "original_overlap", "expanded_overlap"]].head(10)

query  \
0                                                                             on answering a question that no one has asked   
1                                              how much domain expertise and network does a special issue guest editor need   
2                                                          does overhaul need to touch with his hands to activate his quirk   
3                                                                                 why did kanon reincarnate in another race   
4                                                                             how do i disallow screen sharing for messages   
5                                                                                        how do i search for apps on ios 14   
6  mountain bike shorts has an attached inner pair of shorts w padded linershould i detach the inner shorts from the shorts   
7                                                        trainer bike tire does not go on nicely am i doing something wrong   
8                                                  does bear umbra trigger if it was attached with sovereigns of lost alara   
9                                                                                what happens if i double mangaras tome etb   

                                                                                                 expanded_query  \
0              Could you provide guidance on how to approach answering a question that hasnt been asked before,   
1   What level of domain expertise and professional network is required for a special issue guest editor in the   
2      Can you explain if the characters ability to perform a quirk requires manual activation through physical   
3                                     Im curious about the reasons behind Kanons reincarnation into a different   
4                        How can I prevent others from sharing my screen while Im sending messages on my device   
5                                   How can I find and download new apps for iOS 14 that are popular among tech   
6                           Im looking for advice on whether to remove the inner padded liners from my mountain   
7                                                  Ive been having trouble with my trainer bike tire; it doesnt   
8                                     Im sorry, but it seems like there might be a misunderstanding or a mix-up   
9                               Im sorry, but it seems like there might be a misunderstanding or a typo in your   

   original_overlap  expanded_overlap  
0          0.777778          0.812500  
1          1.000000          0.888889  
2          0.900000          0.750000  
3          0.857143          0.636364  
4          0.750000          0.600000  
5          0.777778          0.812500  
6          0.625000          0.600000  
7          0.846154          0.818182  
8          0.692308          0.692308  
9          0.625000          0.800000

If "expanded_overlap" is lower than "original_overlap", your expanded queries retrieve worse-matching documents.

In [ ]:
val_queries_bm25 = val_queries.copy()

def get_bm25_weights(query):
    query_terms = query.split()
    term_frequencies = {}

    lexicon = index.getLexicon()  # Load lexicon once for efficiency

    for term in query_terms:
        if term in lexicon:  # Check if term exists in the index
            lex_entry = lexicon[term]
            term_frequencies[term] = lex_entry.getFrequency()  # Use .getFrequency()
        else:
            term_frequencies[term] = 0  # Assign 0 if term is missing

    return term_frequencies

# Compute BM25 weights for original & expanded queries
val_queries_bm25["bm25_weights_original"] = val_queries_bm25["query"].apply(get_bm25_weights)
val_queries_bm25["bm25_weights_expanded"] = val_queries_bm25["expanded_query"].apply(get_bm25_weights)

# Compute total BM25 frequency for original & expanded queries
val_queries_bm25["total_bm25_freq_original"] = val_queries_bm25["bm25_weights_original"].apply(lambda x: sum(x.values()))
val_queries_bm25["total_bm25_freq_expanded"] = val_queries_bm25["bm25_weights_expanded"].apply(lambda x: sum(x.values()))

# Print BM25 weight comparison with total frequencies
val_queries_bm25[["query", "expanded_query", "bm25_weights_original", "bm25_weights_expanded", "total_bm25_freq_original", "total_bm25_freq_expanded"]].head(10)

query  \
0                                                                             on answering a question that no one has asked   
1                                              how much domain expertise and network does a special issue guest editor need   
2                                                          does overhaul need to touch with his hands to activate his quirk   
3                                                                                 why did kanon reincarnate in another race   
4                                                                             how do i disallow screen sharing for messages   
5                                                                                        how do i search for apps on ios 14   
6  mountain bike shorts has an attached inner pair of shorts w padded linershould i detach the inner shorts from the shorts   
7                                                        trainer bike tire does not go on nicely am i doing something wrong   
8                                                  does bear umbra trigger if it was attached with sovereigns of lost alara   
9                                                                                what happens if i double mangaras tome etb   

                                                                                                 expanded_query  \
0              Could you provide guidance on how to approach answering a question that hasnt been asked before,   
1   What level of domain expertise and professional network is required for a special issue guest editor in the   
2      Can you explain if the characters ability to perform a quirk requires manual activation through physical   
3                                     Im curious about the reasons behind Kanons reincarnation into a different   
4                        How can I prevent others from sharing my screen while Im sending messages on my device   
5                                   How can I find and download new apps for iOS 14 that are popular among tech   
6                           Im looking for advice on whether to remove the inner padded liners from my mountain   
7                                                  Ive been having trouble with my trainer bike tire; it doesnt   
8                                     Im sorry, but it seems like there might be a misunderstanding or a mix-up   
9                               Im sorry, but it seems like there might be a misunderstanding or a typo in your   

                                                                                                                                                                                 bm25_weights_original  \
0                                                                                            {'on': 428, 'answering': 0, 'a': 1, 'question': 2083, 'that': 6, 'no': 0, 'one': 0, 'has': 0, 'asked': 0}   
1                               {'how': 3, 'much': 0, 'domain': 80, 'expertise': 0, 'and': 4, 'network': 130, 'does': 0, 'a': 1, 'special': 579, 'issue': 0, 'guest': 48, 'editor': 106, 'need': 2691}   
2                                                                        {'does': 0, 'overhaul': 9, 'need': 2691, 'to': 52, 'touch': 306, 'with': 0, 'his': 0, 'hands': 0, 'activate': 0, 'quirk': 74}   
3                                                                                                              {'why': 2, 'did': 0, 'kanon': 3, 'reincarnate': 0, 'in': 14, 'another': 0, 'race': 285}   
4                                                                                                    {'how': 3, 'do': 0, 'i': 2, 'disallow': 15, 'screen': 189, 'sharing': 0, 'for': 0, 'messages': 0}   
5                                                                                                      {'how': 3, 'do': 0, 'i': 2, 'search': 440, 'for': 0, 'apps': 0, 'on': 428, 'ios': 0, '14': 439}   
6  {'mountain': 187, 'bike': 193, 'short

### Personalization Model

The personalized model we are going to create takes into account two different factors for assessing the relevance of a document, in the following order:

- the similarity between the author's tags history (including the tags of the current question) and each of the answerers' tags histories (excluding the tags in the current question). This provides a measure of the shared interests between the author and each user who answered them: the higher the compatibility, the higher the score;

- the similarity between the author's presentation of himself and the answerers' presentations, again to show possible common profile features.

The main idea is to exploit RS techniques like precomputed matrices to retrieve similarity scores that can be combined with baseline retrieval methods. In particular, we will precompute user-user similarity matrices, whose aim is to identify share dinterests between use profiles.

In [ ]:
def combine_author_tags(df):
    combined_author_tags = []

    for _, query_row in df.iterrows():
        user_id = query_row['user_id']
        query_id = query_row['qid']
        author_tags = query_row['tags']
        tags_history = query_row['tags_history']

        # Handle malformed tags_history or empty string
        if tags_history:
            # Split tags_history by spaces to get separate "list-like" strings
            tags_history_list = tags_history.split("] [")
            # Remove the square brackets and convert each part into a list of tags
            author_history = []
            for tag_str in tags_history_list:
                tag_str = tag_str.strip("[]")  # Remove square brackets
                author_history.extend(tag_str.split(', '))  # Split by comma and space
        else:
            author_history = []

        # Combine current tags and history
        combined_tags = set(author_tags) | set(author_history)

        # Remove duplicates and sort alphabetically
        combined_tags_sorted = sorted(combined_tags)  # Returns list of all tags for the author, previous and current, without duplicates, sorted by alphabetical order

        # Append the data for this row
        combined_author_tags.append({
            'user_id': user_id,
            'qid': query_id,
            'author_tags': author_tags,
            'tags_history': tags_history,
            'author_history': author_history,
            'combined_tags': combined_tags_sorted  # Sorted combined tags
        })

    # Create a DataFrame from the list of dictionaries
    combined_df = pd.DataFrame(combined_author_tags)

    return combined_df

In [ ]:
val_queries_history_combined = combine_author_tags(val_queries_history)

In [ ]:
val_queries_history_combined

user_id                 qid  \
0   1582241     academia_143743   
1    935589     academia_148899   
2     59256         anime_56513   
3     59256         anime_59459   
4    331923        apple_408963   
..      ...                 ...   
93  4345338      judaism_110801   
94  1582241  christianity_75499   
95   923667       gaming_363535   
96  2516845      skeptics_47727   
97  3425570      politics_53742   

                                               author_tags  \
0                  [publications, publishability, history]   
1                   [publications, editors, special-issue]   
2                                       [my-hero-academia]   
3                              [mao-gakuin-no-futekigosha]   
4                               [security, screen-sharing]   
..                                                     ...   
93  [parshanut-torah-comment, shevatim-12-tribes, vayechi]   
94                                [catholicism, canon-law]   
95                                       [dragon-quest-xi]   
96                               [united-states, politics]   
97         [united-states, police, civil-rights, currency]   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      

The following dataset was the outcome of a merging between the corpus of answers and the asnwers dataframe, with the aim of retrieving answerer ids for each answer.

In [ ]:
! gdown 16tMg1YBh6vwXfr-Au29hTXtLu8fA7qI0

Downloading...
From: https://drive.google.com/uc?id=16tMg1YBh6vwXfr-Au29hTXtLu8fA7qI0
To: /content/extented_corpus_df.csv
100% 13.7M/13.7M [00:00<00:00, 107MB/s] 


In [ ]:
import pandas as pd
answers  = pd.read_csv("/content/PIR_data/answers.csv")
extended_corpus_df = pd.read_csv('/content/extented_corpus_df.csv')
questions  = pd.read_csv("/content/PIR_data/questions.csv")

<ipython-input-97-c5c8534a20eb>:2: DtypeWarning: Columns (1,6,8) have mixed types. Specify dtype option on import or set low_memory=False.
  answers  = pd.read_csv("/content/PIR_data/answers.csv")
<ipython-input-97-c5c8534a20eb>:4: DtypeWarning: Columns (1,2,5,6,7,8,12,13) have mixed types. Specify dtype option on import or set low_memory=False.
  questions  = pd.read_csv("/content/PIR_data/questions.csv")


In [ ]:
answers

Id             CreationDate  Score  Title  Tags  \
0               writers_8  2010-11-18T20:45:45.533    9.0    NaN   NaN   
1              writers_10  2010-11-18T20:46:43.780    9.0    NaN   NaN   
2              writers_14  2010-11-18T20:49:53.847    5.0    NaN   NaN   
3              writers_15  2010-11-18T20:50:16.683   18.0    NaN   NaN   
4              writers_16  2010-11-18T20:51:07.537   15.0    NaN   NaN   
...                   ...                      ...    ...    ...   ...   
52136043  academia_189056  2022-09-24T19:56:46.960    1.0    NaN   NaN   
52136044  academia_189057  2022-09-24T22:53:15.580    1.0    NaN   NaN   
52136045  academia_189060  2022-09-25T02:35:24.623    3.0    NaN   NaN   
52136046  academia_189061  2022-09-25T02:50:31.710    1.0    NaN   NaN   
52136047  academia_189062  2022-09-25T03:12:20.750    0.0    NaN   NaN   

          CommentCount         ParentId   AccountId  \
0                  0.0        writers_1    225829.0   
1                  0.0        writers_5     66721.0   
2                  0.0        writers_7    198391.0   
3                  3.0        writers_1     94574.0   
4                  9.0        writers_2     66721.0   
...                ...              ...         ...   
52136043           0.0  academia_188775   3930467.0   
52136044           0.0   academia_79859   4462009.0   
52136045           2.0  academia_188774  14891659.0   
52136046           0.0  academia_187307  14891659.0   
52136047           0.0  academia_189047  14891659.0   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            Text  
0                                                                                                                                                                                     

In [ ]:
answers = answers[['Id', 'Score', 'ParentId', 'AccountId']]
answers.columns = ['answer_id', 'answer_score', 'qid', 'answerer_id']

In [ ]:
answers

answer_id  answer_score              qid  answerer_id
0               writers_8           9.0        writers_1     225829.0
1              writers_10           9.0        writers_5      66721.0
2              writers_14           5.0        writers_7     198391.0
3              writers_15          18.0        writers_1      94574.0
4              writers_16          15.0        writers_2      66721.0
...                   ...           ...              ...          ...
52136043  academia_189056           1.0  academia_188775    3930467.0
52136044  academia_189057           1.0   academia_79859    4462009.0
52136045  academia_189060           3.0  academia_188774   14891659.0
52136046  academia_189061           1.0  academia_187307   14891659.0
52136047  academia_189062           0.0  academia_189047   14891659.0

[52136048 rows x 4 columns]

In [ ]:
extended_corpus_df

Unnamed: 0            docno  \
0              0     writers_2010   
1              1     writers_2018   
2              2     writers_2023   
3              3     writers_2026   
4              4     writers_2095   
...          ...              ...   
9393        9393  academia_138970   
9394        9394  academia_139396   
9395        9395  academia_143753   
9396        9396  academia_148936   
9397        9397  academia_185179   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  text  \
0                                                                                                                                          TL;DRIf you're going to do present tense do it for a good reason and mitigate the downsides.Long versionPresent tense lends a sense of immediacy to the work and als

In [ ]:
questions

Id AcceptedAnswerId             CreationDate  Score  \
0                writers_1       writers_15  2010-11-18T20:40:32.857   31.0   
1                writers_2       writers_16  2010-11-18T20:42:31.513   23.0   
2                writers_3       writers_31  2010-11-18T20:43:28.903   36.0   
3                writers_5              NaN  2010-11-18T20:43:59.693   34.0   
4                writers_7       writers_85  2010-11-18T20:45:44.067   23.0   
...                    ...              ...                      ...    ...   
143108974  academia_189050              NaN  2022-09-24T08:44:16.210   -2.0   
143108975  academia_189051              NaN  2022-09-24T12:22:05.380    1.0   
143108976  academia_189052              NaN  2022-09-24T12:26:21.210    4.0   
143108977  academia_189058              NaN  2022-09-24T23:54:35.830    1.0   
143108978  academia_189059              NaN  2022-09-25T00:32:58.420    0.0   

           ViewCount  \
0             1597.0   
1            10087.0   
2              812.0   
3             4340.0   
4             1045.0   
...              ...   
143108974       47.0   
143108975       80.0   
143108976      181.0   
143108977       49.0   
143108978       21.0   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  

In [ ]:
questions = questions[['Id', 'AcceptedAnswerId', 'CreationDate', 'Tags', 'AccountId', 'Community']]
questions.columns = ['qid', 'best_answer_id', 'question_date', 'tags', 'author_id', 'community']

In [ ]:
questions

qid best_answer_id            question_date  \
0                writers_1     writers_15  2010-11-18T20:40:32.857   
1                writers_2     writers_16  2010-11-18T20:42:31.513   
2                writers_3     writers_31  2010-11-18T20:43:28.903   
3                writers_5            NaN  2010-11-18T20:43:59.693   
4                writers_7     writers_85  2010-11-18T20:45:44.067   
...                    ...            ...                      ...   
143108974  academia_189050            NaN  2022-09-24T08:44:16.210   
143108975  academia_189051            NaN  2022-09-24T12:22:05.380   
143108976  academia_189052            NaN  2022-09-24T12:26:21.210   
143108977  academia_189058            NaN  2022-09-24T23:54:35.830   
143108978  academia_189059            NaN  2022-09-25T00:32:58.420   

                                                      tags   author_id  \
0                           <resources><first-time-author>      1335.0   
1              <fiction><grammatical-person><third-person>      1335.0   
2                               <publishing><novel><agent>    496961.0   
3             <plot><short-story><planning><brainstorming>    174535.0   
4                             <fiction><genre><categories>    496961.0   
...                                                    ...         ...   
143108974                                          <china>  26368528.0   
143108975       <advisor><application><postdocs><preprint>   2524383.0   
143108976  <publications><research-process><writing-style>    947356.0   
143108977             <phd><advisor><interpersonal-issues>   8286143.0   
143108978                        <authorship><affiliation>  26434421.0   

          community  
0           writers  
1           writers  
2           writers  
3           writers  
4           writers  
...             ...  
143108974  academia  
143108975  academia  
143108976  academia  
143108977  academia  
143108978  academia  

[143108979 rows x 6 columns]

We want to retrieve the history of tags of all possible answerers, which are all the users who wrote the answers appearing as 'docno' in corpus_df. The extended version of the corpus already includes the answerers' ids. From the answers complete dataset we can retrieve, for each answerer in the extended corpus, a list of all other answers they wrote. Answers also already indicates the question each answer is related to, so, for each answerer in the extended corpus we can retrieve a list of questions they answered to overall. Now, not all of these questions can be used as history, due to temporal constraints.

We cannot use as history queries asked in the val_queries df, or after (test_queries). Then, we also need to remove all answers to queries written AFTER the queries in val_queries.

In [ ]:
# create filter for questions keeping only the questions in val_queries and related answers -> get timestamp of those questions

val_queries_dates = questions[
    (questions['qid'].isin(val_qrels['qid'])) &
    (questions['best_answer_id'].isin(val_qrels['docno']))
]

val_queries_dates

qid      best_answer_id            question_date  \
9683            writers_51676       writers_51679  2020-06-25T13:57:21.757   
10262           writers_54275       writers_54323  2020-12-30T21:34:00.807   
37886        workplace_158399    workplace_158416  2020-05-21T07:34:19.667   
38685        workplace_163954    workplace_163955  2020-09-16T07:45:33.573   
46659      vegetarianism_2203  vegetarianism_2249  2020-07-11T21:48:31.210   
...                       ...                 ...                      ...   
143043337        apple_408963        apple_408965  2020-12-15T20:46:16.463   
143068027         anime_56513         anime_56712  2020-01-18T18:01:25.150   
143068381         anime_59459         anime_59463  2020-08-31T12:37:37.880   
143099575     academia_143743     academia_143753  2020-02-03T05:38:49.307   
143100628     academia_148899     academia_148936  2020-05-09T09:10:08.400   

                                                               tags  \
9683                                       <copyright><programming>   
10262                                         <citations><chapters>   
37886      <communication><job-offer><resignation><careers><europe>   
38685           <communication><performance-reviews><salary-review>   
46659                   <scientific-studies><medicine><plant-based>   
...                                                             ...   
143043337                                <security><screen-sharing>   
143068027                                        <my-hero-academia>   
143068381                               <mao-gakuin-no-futekigosha>   
143099575                   <publications><publishability><history>   
143100628                    <publications><editors><special-issue>   

           author_id      community  
9683          7879.0        writers  
10262      3972996.0        writers  
37886      3305982.0      workplace  
38685      1068606.0      workplace  
46659      1532620.0  vegetarianism  
...              ...            ...  
143043337   331923.0          apple  
143068027    59256.0          anime  
143068381    59256.0          anime  
143099575  1582241.0       academia  
143100628   935589.0       academia  

[98 rows x 6 columns]

We first filter the questions to valid ones (temporally), then merge with answers.

In [ ]:
# Convert creationdate to datetime format
questions['question_date'] = pd.to_datetime(questions['question_date'], errors='coerce')
val_queries_dates['question_date'] = pd.to_datetime(val_queries_dates['question_date'], errors='coerce')

<ipython-input-106-b8aa3cb17643>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  questions['question_date'] = pd.to_datetime(questions['question_date'], errors='coerce')
<ipython-input-106-b8aa3cb17643>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  val_queries_dates['question_date'] = pd.to_datetime(val_queries_dates['question_date'], errors='coerce')


In [ ]:
# Drop rows with NaT (invalid dates) in the 'creationdate' column
questions = questions.dropna(subset=['question_date'])
val_queries_dates = val_queries_dates.dropna(subset=['question_date'])

In [ ]:
# Find the least recent (earliest) date in invalid_questions
min_invalid_date = val_queries_dates['question_date'].min()

# Keep only rows where creationdate is before min_invalid_date
filtered_questions = questions[questions['question_date'] < min_invalid_date]

# Optionally, free up memory if needed
#del questions  # Remove old DataFrame to save memory

In [ ]:
filtered_questions

qid   best_answer_id           question_date  \
0                writers_1       writers_15 2010-11-18 20:40:32.857   
1                writers_2       writers_16 2010-11-18 20:42:31.513   
2                writers_3       writers_31 2010-11-18 20:43:28.903   
3                writers_5              NaN 2010-11-18 20:43:59.693   
4                writers_7       writers_85 2010-11-18 20:45:44.067   
...                    ...              ...                     ...   
143099202  academia_142229              NaN 2019-12-31 22:04:00.107   
143099203  academia_142230              NaN 2019-12-31 22:28:54.030   
143099204  academia_142232              NaN 2019-12-31 22:48:26.870   
143099205  academia_142235              NaN 2019-12-31 23:45:05.610   
143099206  academia_142237  academia_142239 2020-01-01 01:12:29.333   

                                                                                     tags  \
0                                                          <resources><first-time-author>   
1                                             <fiction><grammatical-person><third-person>   
2                                                              <publishing><novel><agent>   
3                                            <plot><short-story><planning><brainstorming>   
4                                                            <fiction><genre><categories>   
...                                                                                   ...   
143099202  <advisor><research-undergraduate><publishability><deadlines><negative-results>   
143099203         <publications><graduate-admissions><career-path><physics><early-career>   
143099204                                                               <phd><conference>   
143099205                                             <publications><writing><humanities>   
143099206                                                    <publications><proofreading>   

            author_id community  
0              1335.0   writers  
1              1335.0   writers  
2            496961.0   writers  
3            174535.0   writers  
4            496961.0   writers  
...               ...       ...  
143099202  17429992.0  academia  
143099203  11077258.0  academia  
143099204  17430116.0  academia  
143099205  17430249.0  academia  
143099206  10849559.0  academia  

[23542031 rows x 6 columns]

In [ ]:
# Filter answers where 'AccountId == answerer_id' from extended_corpus_df
filtered_answers = answers[answers['answerer_id'].isin(extended_corpus_df['answerer_id'])]
filtered_answers

answer_id  answer_score              qid  answerer_id
1              writers_10           9.0        writers_5      66721.0
2              writers_14           5.0        writers_7     198391.0
4              writers_16          15.0        writers_2      66721.0
9              writers_26          14.0        writers_5      74379.0
13             writers_32          33.0       writers_18      66721.0
...                   ...           ...              ...          ...
52136035  academia_189044          14.0  academia_189043    9466756.0
52136037  academia_189046           8.0  academia_189040     512142.0
52136038  academia_189048          41.0  academia_189040    3745843.0
52136040  academia_189053           4.0  academia_189051   11182787.0
52136042  academia_189055           6.0  academia_189052    2970583.0

[36119801 rows x 4 columns]

In [ ]:
answers_no_test = filtered_answers[~(
    (filtered_answers['qid'].isin(test_qrels['qid'])) &
    (filtered_answers['answer_id'].isin(test_qrels['docno']))
)]

In [ ]:
answers_no_test

answer_id  answer_score              qid  answerer_id
1              writers_10           9.0        writers_5      66721.0
2              writers_14           5.0        writers_7     198391.0
4              writers_16          15.0        writers_2      66721.0
9              writers_26          14.0        writers_5      74379.0
13             writers_32          33.0       writers_18      66721.0
...                   ...           ...              ...          ...
52136035  academia_189044          14.0  academia_189043    9466756.0
52136037  academia_189046           8.0  academia_189040     512142.0
52136038  academia_189048          41.0  academia_189040    3745843.0
52136040  academia_189053           4.0  academia_189051   11182787.0
52136042  academia_189055           6.0  academia_189052    2970583.0

[36119703 rows x 4 columns]

In [ ]:
answers_no_both = answers_no_test[~(
    (answers_no_test['qid'].isin(val_qrels['qid'])) &
    (answers_no_test['answer_id'].isin(val_qrels['docno']))
)]

In [ ]:
answers_no_both

answer_id  answer_score              qid  answerer_id
1              writers_10           9.0        writers_5      66721.0
2              writers_14           5.0        writers_7     198391.0
4              writers_16          15.0        writers_2      66721.0
9              writers_26          14.0        writers_5      74379.0
13             writers_32          33.0       writers_18      66721.0
...                   ...           ...              ...          ...
52136035  academia_189044          14.0  academia_189043    9466756.0
52136037  academia_189046           8.0  academia_189040     512142.0
52136038  academia_189048          41.0  academia_189040    3745843.0
52136040  academia_189053           4.0  academia_189051   11182787.0
52136042  academia_189055           6.0  academia_189052    2970583.0

[36119605 rows x 4 columns]

In [ ]:
answers_no_both = answers_no_both[(
    (answers_no_both['qid'].isin(filtered_questions['qid']))
)]

In [ ]:
answers_no_both

answer_id  answer_score              qid  answerer_id
1              writers_10           9.0        writers_5      66721.0
2              writers_14           5.0        writers_7     198391.0
4              writers_16          15.0        writers_2      66721.0
9              writers_26          14.0        writers_5      74379.0
13             writers_32          33.0       writers_18      66721.0
...                   ...           ...              ...          ...
52134469  academia_186302           0.0  academia_112258     262150.0
52134567  academia_186462           0.0   academia_10214       7274.0
52134623  academia_186561           3.0   academia_46346    4194043.0
52134665  academia_186631           0.0   academia_65340    4194043.0
52135731  academia_188529           0.0   academia_54577    3941049.0

[5845355 rows x 4 columns]

Now we can finally filter questions too by keeping only qid in answers_no_both, then merge.

In [ ]:
filtered_questions_val = filtered_questions[filtered_questions['qid'].isin(answers_no_both['qid'])]

In [ ]:
filtered_questions_val

qid   best_answer_id           question_date  \
0                writers_1       writers_15 2010-11-18 20:40:32.857   
1                writers_2       writers_16 2010-11-18 20:42:31.513   
2                writers_3       writers_31 2010-11-18 20:43:28.903   
3                writers_5              NaN 2010-11-18 20:43:59.693   
4                writers_7       writers_85 2010-11-18 20:45:44.067   
...                    ...              ...                     ...   
143099202  academia_142229              NaN 2019-12-31 22:04:00.107   
143099203  academia_142230              NaN 2019-12-31 22:28:54.030   
143099204  academia_142232              NaN 2019-12-31 22:48:26.870   
143099205  academia_142235              NaN 2019-12-31 23:45:05.610   
143099206  academia_142237  academia_142239 2020-01-01 01:12:29.333   

                                                                                     tags  \
0                                                          <resources><first-time-author>   
1                                             <fiction><grammatical-person><third-person>   
2                                                              <publishing><novel><agent>   
3                                            <plot><short-story><planning><brainstorming>   
4                                                            <fiction><genre><categories>   
...                                                                                   ...   
143099202  <advisor><research-undergraduate><publishability><deadlines><negative-results>   
143099203         <publications><graduate-admissions><career-path><physics><early-career>   
143099204                                                               <phd><conference>   
143099205                                             <publications><writing><humanities>   
143099206                                                    <publications><proofreading>   

            author_id community  
0              1335.0   writers  
1              1335.0   writers  
2            496961.0   writers  
3            174535.0   writers  
4            496961.0   writers  
...               ...       ...  
143099202  17429992.0  academia  
143099203  11077258.0  academia  
143099204  17430116.0  academia  
143099205  17430249.0  academia  
143099206  10849559.0  academia  

[12862560 rows x 6 columns]

Let's try to group by 'qid', joining the other attributes to understand if there are duplicates or just different answers for the same questions.

In [ ]:
# Define the aggregation logic
tags_per_question = filtered_questions_val.groupby('qid').agg({
    'tags': lambda x: ','.join(x.dropna().astype(str)),  # Join tags with a comma
    'community': 'first'  # Assuming the community is the same for each qid
}).reset_index()


In [ ]:
tags_per_question

qid  \
0            academia_1   
1        academia_10001   
2       academia_100013   
3       academia_100017   
4       academia_100020   
...                 ...   
557962      writers_997   
557963     writers_9986   
557964     writers_9991   
557965     writers_9995   
557966     writers_9997   

                                                                                tags  \
0                                                          <job-search><visa><japan>   
1                                                          <publications><copyright>   
2                                       <research-process><graduate-school><advisor>   
3               <graduate-admissions><funding><professorship><email><administration>   
4       <graduate-admissions><graduate-school><advisor><application><united-kingdom>   
...                                                                              ...   
557962                                                          <fiction><viewpoint>   
557963                                                                  <formatting>   
557964                          <creative-writing><character-development><viewpoint>   
557965                                                                  <formatting>   
557966                                                             <editing><poetry>   

       community  
0       academia  
1       academia  
2       academia  
3       academia  
4       academia  
...          ...  
557962   writers  
557963   writers  
557964   writers  
557965   writers  
557966   writers  

[557967 rows x 3 columns]

In [ ]:
tags_per_question.to_csv('tags_per_question.csv', index=False)

In [ ]:
answers_history_val = answers_no_both.merge(
    tags_per_question,
    on='qid',
    how='left',
)

In [ ]:
answers_history_val

answer_id  answer_score              qid  answerer_id  \
0             writers_10           9.0        writers_5      66721.0   
1             writers_14           5.0        writers_7     198391.0   
2             writers_16          15.0        writers_2      66721.0   
3             writers_26          14.0        writers_5      74379.0   
4             writers_32          33.0       writers_18      66721.0   
...                  ...           ...              ...          ...   
5845350  academia_186302           0.0  academia_112258     262150.0   
5845351  academia_186462           0.0   academia_10214       7274.0   
5845352  academia_186561           3.0   academia_46346    4194043.0   
5845353  academia_186631           0.0   academia_65340    4194043.0   
5845354  academia_188529           0.0   academia_54577    3941049.0   

                                                     tags community  
0            <plot><short-story><planning><brainstorming>   writers  
1                            <fiction><genre><categories>   writers  
2             <fiction><grammatical-person><third-person>   writers  
3            <plot><short-story><planning><brainstorming>   writers  
4                                               <editing>   writers  
...                                                   ...       ...  
5845350                <paper-submission><extended-paper>  academia  
5845351                 <teaching><audio-video-recording>  academia  
5845352  <phd><career-path><professorship><international>  academia  
5845353                             <peer-review><ethics>  academia  
5845354                    <peer-review><self-plagiarism>  academia  

[5845355 rows x 6 columns]

In [ ]:
answerers_tag_history = answers_history_val.groupby('answerer_id').agg({
    'tags': lambda x: ', '.join(x.dropna().astype(str)),  # Join tags with a comma
    'community': lambda x: ', '.join(x.dropna().astype(str))  # Join communities with a comma
}).reset_index()

# for val, also contains the communities the answerers have written answers for

In [ ]:
answerers_tag_history

answerer_id  \
0            41.0   
1           146.0   
2           213.0   
3           224.0   
4           244.0   
...           ...   
3674   22001670.0   
3675   22135094.0   
3676   23648463.0   
3677   24278800.0   
3678   24520713.0   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         

We finally have successfully retrieved the answerers' tag histories!!!

The total number of users in the corpus of answers was originally 3689. Not a big problem, it means that a few users probably answered their first question in "validation time" or in "test time" and therefore have no previously answered questions to use as history.

In [ ]:
total_answerers = extended_corpus_df[['answerer_id']].drop_duplicates()

In [ ]:
total_answerers

answerer_id
0         74379.0
1        507794.0
2        528857.0
3        114006.0
5        342002.0
...           ...
9388    2950649.0
9390    1550338.0
9392   11182787.0
9395    6848536.0
9397    1110667.0

[3690 rows x 1 columns]

In [ ]:
total_answerers['answerer_id'].isnull().sum()

1

We have 1 user among the possible answerers we don't know the id of. We can drop it.

In [ ]:
total_answerers = total_answerers.dropna(subset=['answerer_id'])

Now we only want to merge th answerer_id column of the grouped df with the available tag histories, so that for each possible answerer we either have a history or NaN.

In [ ]:
final_ans_history = total_answerers.merge(
    answerers_tag_history[['answerer_id', 'tags']],
    on='answerer_id',
    how='left'
)

In [ ]:
final_ans_history

answerer_id  \
0         74379.0   
1        507794.0   
2        528857.0   
3        114006.0   
4        342002.0   
...           ...   
3684    2950649.0   
3685    1550338.0   
3686   11182787.0   
3687    6848536.0   
3688    1110667.0   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         

In [ ]:
# Function to clean and process tag histories
def process_tag_history(tag_history):
    if pd.isna(tag_history):  # Handle NaN values
        return set()
    tags = re.findall(r'<(.*?)>', tag_history)  # Extract tags from <>
    return set(tags)  # Convert to set to remove duplicates

# Apply the function
final_ans_history['tags'] = final_ans_history['tags'].apply(process_tag_history)

In [ ]:
final_ans_history

answerer_id  \
0         74379.0   
1        507794.0   
2        528857.0   
3        114006.0   
4        342002.0   
...           ...   
3684    2950649.0   
3685    1550338.0   
3686   11182787.0   
3687    6848536.0   
3688    1110667.0   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      tags  
0                                                                                                                                                                                                                                                                                                                                                                                                                     {broiling, stove, microwave, joint-account, credit-score, tasting, first-time-home-buyer, pumpkin, soy, mortgage, comparison, tone, vinegar, resources, fantasy, debt, crust, caribbean-cuisine, music, portfolio, night-time, fruit, college, smell, cooking-time, noodles, movies, seasoning, coffee, translation, dry-aging, batter, sugar, drinks, sharpening, united-kingdom, dough, quotes, dialogue, rate-of-return, cheese, lifestyle, pennsylvania, crab, process, language, sorbet, non-stick, baking, investing, dutch-oven, pita, retirement-plan, spending, tomatoes, home-loan, book-rec, fresh, tools, sourdough, chocolate, business-writing, dairy-free, reduction, third-person, career, kneading, editing, science-fiction, newborn, allergy, marriage, seafood, websites, wheat, activities, crepe, organization, turkey, broth, grammar, bottle-feeding, description, plot, juicing, jam, pan, down-payment, hitting, flatbread, barbecue, cilantro, purchase, stocks, dairy, cookbook, eating, mother, starting-out-investing, reheating, ...}  
1                                                                                                                                                                                           {headlines, self-publishing, scriptwriting, book-collecting, indexing, dragonriders-of-pern, degree, the-great-gatsby, chapters, graphics, tone, categories, resources, grammatical-person, myersbriggs, fantasy, letter, memoir, dante-alighieri, narrative, anne-mccaffrey, footnotes, multilingual, creative-commons, time-management, narrator, translation, the-great-divorce, apa, torture, conventions, climax, suzanne-collins, proofreading, quotes, the-eagles, dialogue, theme, biography, cliches, process, language, to-kill-a-mockingbird, goal, alan-turing, erotica, shel-silverstein, charlie-and-the-chocolate-factory, paranormal, e-l-james, book-rec, comedy, tools, monsters, lyrics, rhythm,

In [ ]:
authors_tags = val_queries_history_combined[['user_id', 'combined_tags']] # choose the right columns

In [ ]:
authors_tags

user_id  \
0   1582241   
1    935589   
2     59256   
3     59256   
4    331923   
..      ...   
93  4345338   
94  1582241   
95   923667   
96  2516845   
97  3425570   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             combined_tags  
0                                                                                                                                                                                                                                    ['18th-century', '19th-century', 'age-of-discovery', 'age-of-sail', 'agriculture', 'aircraft', 'alaska', 'alcohol', 'ambiguity', 'american-english', 'ancestry.com', 'animals', 'annulment', 'architecture', 'art', 'artillery', 'avocado', 'baptism', 'building', 'business-history', 'california', 'canon-law', 'caribbean', 'castles', 'catholic-church', 'catholicism', 'cd', 'ceremony', 'chile', 'china', 'chinese', 'chronology', 'church', 'church-hierarchy', 'citation', 'citation-style', 'citations', 'cold-weather', 'colonial-america', 'colonization', 'communication', 'computational-linguistics', 'conversion', 'copyright', 'crime', 'data-storage', 'death', 'decolonization', 'desert', 'development', 'disability', 'disasters', 'drugs', 'eastern-orthodox', 'economy', 'education', 'election', 'electoral-system', 'emotional-responses', 'england', 'ethics', 'ethiopia', 'ethnicity', 'exams', 'exploration', 'famous-people', 'fans', 'fence', 'festival', 'flags', 'food', 'forestry', 'funding', 'fur-trade', 'gold', 'government', 'graduate-admissions', 'graphics', 'ground-cover', 'harvesting', 'hawaii', 'health', 'historical-research', 'historiography', 'holidays', 'home-automation', 'hungary', 'hvac', 'identification', 'identity-documents', 'immigration', 'independent-study', 'individuals', 'indoors', 'international-students', 'inventions', 'japan', 'kamchatka', 'korea', 'labour-history', ...]  
1                                                                                                                                                                                       ['20th-century', 'academic-writing', 'access-rights', 'accommodation', 'acknowledgement', 'adjectives', 'africa', 'air-travel', 'airport-transfer', 'alaska', 'alberta', 'alexei-navalny', 'amsterdam', 'analysis', 'anchor', 'anthropology', 'antisemitism', 'architecture', 'arctic', 'arrival', 'article-50', 'atm', 'backcountry', 'backpacking', 'backpacks', 'banking', 'bear-spray', '

In [ ]:
def process_tag_list(tag_list):

    if isinstance(tag_list, float) and pd.isna(tag_list):  # Handle NaN values safely
        return set()  # Return an empty set

    if isinstance(tag_list, str):
        try:
            tag_list = eval(tag_list)  # Convert string representation of list to actual list
        except:
            return set()  # Return an empty set if eval fails

    if isinstance(tag_list, list):
        return set(tag_list)  # Convert to a set to remove duplicates

    return set()  # Fallback in case of unexpected formats


# Apply function to the column containing combined tags
authors_tags['combined_tags'] = authors_tags['combined_tags'].apply(process_tag_list)
authors_tags

<ipython-input-136-5a65f8e5db75>:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  authors_tags['combined_tags'] = authors_tags['combined_tags'].apply(process_tag_list)


user_id  \
0   1582241   
1    935589   
2     59256   
3     59256   
4    331923   
..      ...   
93  4345338   
94  1582241   
95   923667   
96  2516845   
97  3425570   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     combined_tags  
0                                                                                                                                                                                                                                                         {'agriculture', 'social-history', 'numismatics', 'festival', 'alcohol', 'land', 'noise-reduction', 'weapons', 'flags', 'political-theory', 'native-americans', 'chronology', 'tradition', 'ceremony', 'pest-damage', 'warfare', 'catholic-church', 'salary', 'funding', 'china', 'food', 'economy', 'political-party', 'colonization', 'fence', 'ethics', 'hungary', 'education', 'military', 'artillery', 'writing', 'health', 'korea', 'vines', 'cold-weather', 'desert', 'research-assistantship', 'citations', 'religious-orders', 'copyright', 'citation-style', 'harvesting', 'canon-law', 'japan', 'pests', 'research-undergraduate', 'sex', 'aircraft', 'death', 'data-storage', 'law', 'privacy-plants', 'exploration', 'age-of-discovery', 'patron-saints', 'castles', 'nautical', 'cd', 'naval', 'slavery', 'california', 'communication', 'ethnicity', 'avocado', 'material-culture', '19th-century', 'holidays', 'legislature', 'settlement', 'london', 'art', 'independent-study', 'treaties', 'publishers', 'election', 'emotional-responses', 'indoors', 'library', 'eastern-orthodox', 'crime', 'church', 'resource', 'historical-research', 'priesthood', 'orthodoxism', 'age-of-sail', 'disasters', 'international-students', 'disability', 'sexuality', 'conversion', 'citation', 'electoral-system', 'ethiopia', 'identification', 'security', 'graduate-admissions', 'microfilm', 'toponymy', publishability, ...}  
1                                                                                                                                                                                                                                                        {'draisine', 'company-policy', 'transit', 'head-of-state', 'biology', 'literature', 'passenger-rights', 'human-waste', 'children', 'africa', 'territory', 'acknowledgement', 'chairing', 'colonization', 'noise', 'rent', 'energy-efficiency', 'residency', 'open-access', 'north-korea', 'deutsche-bahn', '

In [ ]:
final_ans_history['answerer_id'] = final_ans_history['answerer_id'].astype(int)

In [ ]:
final_ans_history

answerer_id  \
0           74379   
1          507794   
2          528857   
3          114006   
4          342002   
...           ...   
3684      2950649   
3685      1550338   
3686     11182787   
3687      6848536   
3688      1110667   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      tags  
0                                                                                                                                                                                                                                                                                                                                                                                                                     {broiling, stove, microwave, joint-account, credit-score, tasting, first-time-home-buyer, pumpkin, soy, mortgage, comparison, tone, vinegar, resources, fantasy, debt, crust, caribbean-cuisine, music, portfolio, night-time, fruit, college, smell, cooking-time, noodles, movies, seasoning, coffee, translation, dry-aging, batter, sugar, drinks, sharpening, united-kingdom, dough, quotes, dialogue, rate-of-return, cheese, lifestyle, pennsylvania, crab, process, language, sorbet, non-stick, baking, investing, dutch-oven, pita, retirement-plan, spending, tomatoes, home-loan, book-rec, fresh, tools, sourdough, chocolate, business-writing, dairy-free, reduction, third-person, career, kneading, editing, science-fiction, newborn, allergy, marriage, seafood, websites, wheat, activities, crepe, organization, turkey, broth, grammar, bottle-feeding, description, plot, juicing, jam, pan, down-payment, hitting, flatbread, barbecue, cilantro, purchase, stocks, dairy, cookbook, eating, mother, starting-out-investing, reheating, ...}  
1                                                                                                                                                                                           {headlines, self-publishing, scriptwriting, book-collecting, indexing, dragonriders-of-pern, degree, the-great-gatsby, chapters, graphics, tone, categories, resources, grammatical-person, myersbriggs, fantasy, letter, memoir, dante-alighieri, narrative, anne-mccaffrey, footnotes, multilingual, creative-commons, time-management, narrator, translation, the-great-divorce, apa, torture, conventions, climax, suzanne-collins, proofreading, quotes, the-eagles, dialogue, theme, biography, cliches, process, language, to-kill-a-mockingbird, goal, alan-turing, erotica, shel-silverstein, charlie-and-the-chocolate-factory, paranormal, e-l-james, book-rec, comedy, tools, monsters, lyrics, rhythm,

First, we need to group the authors_tags by user_id as there are duplicates, and if the combined_tags are different we need to keep the larger set (they are sets of tags, so we assume that if the same user has more than one set assigned, they are likely similar but one maybe misses a few tags -> we want to keep the most complete set).

In [ ]:
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', None)
authors_tags

user_id  \
0    1582241   
1     935589   
2      59256   
3      59256   
4     331923   
5     331923   
6      69157   
7      69157   
8    1077413   
9     507522   
10     30494   
11     30494   
12   3972996   
13   1582241   
14   3972996   
15   3972996   
16     69157   
17    923667   
18   2150876   
19   2150876   
20   1582241   
21   1821810   
22    359320   
23   3972996   
24      1325   
25     59256   
26   4403071   
27   1634774   
28   9101990   
29  12194021   
30  12194021   
31    935589   
32   1582241   
33   1532620   
34   1532620   
35   2516845   
36   3305982   
37    961274   
38    359320   
39   1352706   
40   3832028   
41   6362904   
42    359320   
43   1634774   
44   2150876   
45   1068606   
46     22370   
47   1344292   
48    359320   
49     67390   
50     67390   
51    961274   
52      7879   
53    935589   
54    935589   
55   3690277   
56   3690277   
57    210795   
58   2150876   
59   3972996   
60     17355   
61   4403071   
62   2293919   
63   1077413   
64   1344292   
65   1077413   
66   4403071   
67   4403071   
68    923667   
69    923667   
70   2150876   
71   2150876   
72   1532620   
73   3305982   
74   1068606   
75      7879   
76   3972996   
77   4403071   
78   1077413   
79    906366   
80   2614901   
81    906366   
82  11680930   
83   2516845   
84     30494   
85   1077413   
86    906366   
87   1077413   
88  11680930   
89   2150876   
90   2580331   
91   1077413   
92   1582241   
93   4345338   
94   1582241   
95    923667   
96   2516845   
97   3425570   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           combined_tags  
0                                                                                                                                                                                                                                                                               {'agriculture', 'social-history', 'numismatics', 'festival', 'alcohol', 'land', 'noise-reduction', 'weapons', 'flags', 'political-theory', 'native-americans', 'chronology', 'tradition', 'ceremony', 'pest-damage', 'warfare', 'catholic-church', 'salary', 'funding', 'china', 'food', 'economy', 'political-party', 'colonization', 'fence', 'ethics', 'hungary', 'education', 'military', 'artillery', 'writing', 'health', 'korea', 'vines', 'cold-weather', 'desert', 'research-assistantship', 'ci

In [ ]:
len(authors_tags['user_id'].unique())

40

In [ ]:
len(val_queries['user_id'].unique())

40

They match!

In [ ]:
authors_tags = authors_tags.groupby('user_id').agg({
    'combined_tags': lambda x: max(x, key=len)  # Keep the set with the most tags
}).reset_index()

In [ ]:
pd.reset_option('display.max_colwidth')
pd.reset_option('display.max_rows')
authors_tags

user_id                                      combined_tags
0       1325  {'john-paul-ii', 'revelation', 'urban-gardenin...
1       7879  {'work', 'joshua', 'revelation', 'torchwood', ...
2      17355  {'work', 'multilingualism', 'sexism', 'mahatma...
3      22370  {'winter', 'kitchen', 'malaria', 'synonyms', '...
4      30494  {'three-lakshanas', 'samatha', 'wheel-of-life'...
5      59256  {'tokyo-ghoul', 'dragon-ball-manga', 'portugue...
6      67390  {'display', 'road-bike', 'dns', 'new-girl', 'm...
7      69157  {'circuit-breaker', 'appliances', 'ducts', 'ex...
8     210795  {'grinding', 'chocolate', 'kitchen', 'company-...
9     331923  {'sharing-scheme', 'bike-vs-car', 'auto-bright...
10    359320  {'social-history', 'central-bank', 'diablo-3-b...
11    507522  {'magic-the-gathering', 'steam', 'team-fortres...
12    906366  {'destiny-2', 'passports', 'resume', 'steam-tr...
13    923667  {'emulation', 'diablo-3-barbarian', range, 'du...
14    935589  {'draisine', 'company-policy', 'transit', 'hea...
15    961274  {'bergson', 'emotions', 'buddhism', 'computati...
16   1068606  {'7-wonders-duel', 'a-song-of-ice-and-fire', '...
17   1077413  {'shared-universe', 'life-paths', 'game-design...
18   1344292  {'constantine-city-of-demons', 'the-lord-of-th...
19   1352706  {'bishul-akum', 'mistakes', 'pentateuch-chumas...
20   1532620  {'schism', 'circuit-breaker', 'ecclesiology', ...
21   1582241  {'agriculture', 'social-history', 'numismatics...
22   1634774  {'covenant', 'revelation', 'temple', 'chiasm',...
23   1821810  {'professorship', 'property-taxes', 'jurisdict...
24   2150876  {'airlines', 'synonyms', 'syntax-trees', 'pron...
25   2293919  {'unearthed-arcana', 'fighter', 'shame', 'char...
26   2516845  {'starting-out-investing', 'resume', 'steam-tr...
27   2580331  {'puzzle-and-dragons', 'super-smash-bros-melee...
28   2614901  {'russian-federation', 'united-nations', 'temp...
29   3305982  {'russian-federation', 'united-nations', 'soci...
30   3425570  {'etymology', 'vocatives', 'expression-choice'...
31   3690277  {'dark-souls-2', 'the-lord-of-the-rings', 'gro...
32   3832028  {'commentaries', 'homosexuality', 'bo', commen...
33   3972996  {'branches', 'agriculture', 'finance', 'tomato...
34   4345338  {'sukkah', 'bamidbar-parsha', 'mon-manna', 'be...
35   4403071  {'russian-federation', 'united-nations', 'summ...
36   6362904  {'archetype', 'double-weapons', 'weight', 'wea...
37   9101990  {'joshua', 'revelation', 'david', 'kjv', 'jeze...
38  11680930  {'gentiles', 'sukkah', 'parashat-teruma', arch...
39  12194021  {'temple', 'birth', 'ganga', 'practice', 'curs...

#### Tag similarity matrix (user-user)

In [ ]:
# Create an empty matrix with authors as rows and answerers as columns
similarity_matrix = pd.DataFrame(index=authors_tags['user_id'], columns=final_ans_history['answerer_id'], dtype=float)

# Function to compute the similarity
def compute_similarity(author_tags, answerer_tags, author_id, answerer_id):
    if author_id == answerer_id:
        return 0 # mark the pair as "no recommendation"
    # Ensure tags are sets, in case they are still stored as strings
    if isinstance(author_tags, str):
        author_tags = set(author_tags.split(','))
    if isinstance(answerer_tags, str):
        answerer_tags = set(answerer_tags.split(','))
    intersection = author_tags.intersection(answerer_tags)
    return len(intersection) / len(author_tags) if len(author_tags) > 0 else 0

# Iterate over each author and each answerer to compute the similarity
for author_idx, author_row in authors_tags.iterrows():
    author_tags = author_row['combined_tags']  # The tag set for the author
    author_id = author_row['user_id']  # Author's ID
    for answerer_idx, answerer_row in final_ans_history.iterrows():
        answerer_tags = answerer_row['tags']  # The tag set for the answerer
        answerer_id = answerer_row['answerer_id']  # Answerer's ID

        similarity = compute_similarity(author_tags, answerer_tags, author_id, answerer_id)
        similarity_matrix.at[author_id, answerer_id] = similarity

# Now similarity_matrix contains the similarity values
print(similarity_matrix)

answerer_id  74379     507794    528857    114006    342002    113876    \
user_id                                                                   
1325         0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
7879         0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
17355        0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
22370        0.004149  0.000000       0.0  0.000000  0.000000  0.004149   
30494        0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
59256        0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
67390        0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
69157        0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
210795       0.004348  0.000000       0.0  0.000000  0.004348  0.000000   
331923       0.000000  0.000000       0.0  0.006757  0.000000  0.000000   
359320       0.004464  0.000000       0.0  0.000000  0.000000  0.000000   
507522       0.000000  0.

Perfect! We have a score for each user-user pair (40 unique users in val_queries, 3689 unique users in corpus_df). Now let's compute the bm25 scores -> we have to make the scores comparable.

In [ ]:
val_queries

qid                                              query  \
0      academia_143743      on answering a question that no one has asked   
1      academia_148899  how much domain expertise and network does a s...   
2          anime_56513  does overhaul need to touch with his hands to ...   
3          anime_59459          why did kanon reincarnate in another race   
4         apple_408963      how do i disallow screen sharing for messages   
..                 ...                                                ...   
95      judaism_110801                     where were yaakovs sons buried   
96  christianity_75499                   is a catholic canon a prebendary   
97       gaming_363535     what does each statistic do in dragon quest xi   
98      skeptics_47727  did white supremacists mixin with groups prote...   
99      politics_53742  why do us police treat using counterfeit money...   

    user_id  
0   1582241  
1    935589  
2     59256  
3     59256  
4    331923  
..      ...  
95  4345338  
96  1582241  
97   923667  
98  2516845  
99  3425570  

[98 rows x 3 columns]

In [ ]:
val_queries = val_queries[val_queries['query'].str.strip() != '']
val_queries['query'] = val_queries['query'].apply(lambda x: re.sub(r'[^\w\s]', '', x))  # Remove non-word characters
val_queries['query'] = val_queries['query'].apply(lambda x: re.sub(r'\s+', ' ', x))   # Replace multiple spaces with a single space


#### BM25 matrix

In [ ]:
bm25 = pt.BatchRetrieve(index, wmodel="BM25", num_results=10)  # Set a very large limit
bm25_scores_df = bm25.transform(val_queries)
bm25_scores_df

<ipython-input-147-6a0623fdd926>:1: DeprecationWarning: Call to deprecated class BatchRetrieve. (use pt.terrier.Retriever() instead) -- Deprecated since version 0.11.0.
  bm25 = pt.BatchRetrieve(index, wmodel="BM25", num_results=10)  # Set a very large limit


qid  docid             docno  rank      score  \
0    academia_143743    284  workplace_102543     0  15.936678   
1    academia_143743   2513  philosophy_23588     1  13.746749   
2    academia_143743    471       travel_9601     2  13.704156   
3    academia_143743   8336    buddhism_10876     3  13.482151   
4    academia_143743   9262    academia_13612     4  13.225339   
..               ...    ...               ...   ...        ...   
967   politics_53742   1397       scifi_55474     5  14.360995   
968   politics_53742   3743       money_28435     6  14.034960   
969   politics_53742   8398   boardgames_5937     7  13.657581   
970   politics_53742   3828       money_97891     8  13.330742   
971   politics_53742   2106     politics_1133     9  13.244456   

                                                 query  user_id  
0        on answering a question that no one has asked  1582241  
1        on answering a question that no one has asked  1582241  
2        on answering a question that no one has asked  1582241  
3        on answering a question that no one has asked  1582241  
4        on answering a question that no one has asked  1582241  
..                                                 ...      ...  
967  why do us police treat using counterfeit money...  3425570  
968  why do us police treat using counterfeit money...  3425570  
969  why do us police treat using counterfeit money...  3425570  
970  why do us police treat using counterfeit money...  3425570  
971  why do us police treat using counterfeit money...  3425570  

[972 rows x 7 columns]

#### Normalization of precomputed matrices

In [ ]:
from sklearn.preprocessing import MinMaxScaler

def precompute_bm25_scores(index, queries_df):

    bm25 = pt.BatchRetrieve(index, num_results=10)  # Retrieve top 10 results per query
    bm25_scores_df = bm25.transform(queries_df)  # Get BM25 scores

    if not bm25_scores_df.empty:
        scaler = MinMaxScaler(feature_range=(0, 1))
        bm25_scores_df['normalized_score'] = scaler.fit_transform(bm25_scores_df['score'].values.reshape(-1, 1))

    return bm25_scores_df

def precompute_tag_similarity_matrix(tag_similarity_matrix):

    row_max = tag_similarity_matrix.max(axis=1).replace(0, 1)  # Avoid division by zero
    normalized_matrix = tag_similarity_matrix.div(row_max, axis=0)  # Row-wise normalization

    return normalized_matrix

In [ ]:
precomputed_bm25_val = precompute_bm25_scores(index, val_queries)
precomputed_bm25_val

<ipython-input-148-a79c8fe2efd0>:5: DeprecationWarning: Call to deprecated class BatchRetrieve. (use pt.terrier.Retriever() instead) -- Deprecated since version 0.11.0.
  bm25 = pt.BatchRetrieve(index, num_results=10)  # Retrieve top 10 results per query


qid  docid             docno  rank      score  \
0    academia_143743    284  workplace_102543     0  13.346439   
1    academia_143743   2513  philosophy_23588     1  11.093355   
2    academia_143743   4176          law_5712     2  10.021344   
3    academia_143743   8174       buddhism_64     3   9.975864   
4    academia_143743   2974   parenting_30739     4   9.920623   
..               ...    ...               ...   ...        ...   
967   politics_53742   3808       money_69650     5  10.225611   
968   politics_53742   5904        health_933     6   8.722365   
969   politics_53742   1797         rpg_12464     7   8.322850   
970   politics_53742   4244         law_26574     8   8.086206   
971   politics_53742   1282       scifi_21220     9   7.842109   

                                                 query  user_id  \
0        on answering a question that no one has asked  1582241   
1        on answering a question that no one has asked  1582241   
2        on answering a question that no one has asked  1582241   
3        on answering a question that no one has asked  1582241   
4        on answering a question that no one has asked  1582241   
..                                                 ...      ...   
967  why do us police treat using counterfeit money...  3425570   
968  why do us police treat using counterfeit money...  3425570   
969  why do us police treat using counterfeit money...  3425570   
970  why do us police treat using counterfeit money...  3425570   
971  why do us police treat using counterfeit money...  3425570   

     normalized_score  
0            0.283184  
1            0.209749  
2            0.174809  
3            0.173327  
4            0.171526  
..                ...  
967          0.181467  
968          0.132472  
969          0.119450  
970          0.111737  
971          0.103782  

[972 rows x 8 columns]

In [ ]:
normalized_tag_matrix = precompute_tag_similarity_matrix(similarity_matrix)
normalized_tag_matrix

answerer_id  74379     507794    528857    114006    342002    113876    \
user_id                                                                   
1325         0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
7879         0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
17355        0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
22370        0.333333  0.000000       0.0  0.000000  0.000000  0.333333   
30494        0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
59256        0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
67390        0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
69157        0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
210795       0.250000  0.000000       0.0  0.000000  0.250000  0.000000   
331923       0.000000  0.000000       0.0  0.333333  0.000000  0.000000   
359320       0.200000  0.000000       0.0  0.000000  0.000000  0.000000   
507522       0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
906366       0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
923667       0.250000  0.000000       0.0  0.000000  0.000000  0.000000   
935589       0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
961274       0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
1068606      0.666667  0.000000       0.0  0.000000  0.000000  0.000000   
1077413      0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
1344292      0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
1352706      0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
1532620      0.000000  0.333333       0.0  0.333333  0.333333  0.000000   
1582241      0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
1634774      0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
1821810      0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
2150876      0.200000  0.000000       0.0  0.000000  0.000000  0.200000   
2293919      0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
2516845      0.500000  0.000000       0.0  0.000000  0.000000  0.000000   
2580331      0.000000  0.000000       0.0  0.250000  0.000000  0.000000   
2614901      0.200000  0.000000       0.0  0.000000  0.000000  0.200000   
3305982      0.000000  0.000000       0.0  0.000000  0.000000  0.200000   
3425570      0.250000  0.000000       0.0  0.000000  0.000000  0.250000   
3690277      0.666667  0.333333       0.0  0.000000  0.666667  0.333333   
3832028      0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
3972996      0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
4345338      0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
4403071      0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
6362904      0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
9101990      0.000000  0.000000       0.0  0.000000  0.000000  0.000000   
11680930     0.250000  0.000000       0.0  0.000000  0.000000  0.000000   
12194021     0.000000  0.000000       0.0  0.000000  0.000000  0.000000   

answerer_id  528883    100982    5121      71567     ...  5208621   9161525   \
user_id                                              ...                       
1325         0.000000  0.000000  0.000000  0.000000  ...  0.000000  0.000000   
7879         0.000000  0.000000  0.000000  0.000000  ...  0.000000  0.333333   
17355        0.000000  0.000000  0.000000  0.000000  ...  0.000000  0.000000   
22370        0.000000  0.000000  0.000000  0.000000  ...  0.000000  0.000000   
30494        0.000000  0.000000  0.000000  0.000000  ...  0.000000  0.000000   
59256        0.000000  0.000000  0.000000  0.000000  ...  0.000000  0.000000   
67390        0.000000  0.000000  0.000000  0.000000  ...  0.000000  0.000000   
69157        0.000000  0.000000  0.000000  0.000000  ...  0.000000  0.000000   
210795       0.000000  0.000000  0.000000  0.0000

#### Hybrid retrieval

In [ ]:
class CombinedRetriever(pt.transformer.Transformer):
    def __init__(self, precomputed_bm25, normalized_tag_matrix, extended_corpus_df, alpha=0.7):
        self.precomputed_bm25 = precomputed_bm25_val  # Precomputed BM25 scores
        self.normalized_tag_matrix = normalized_tag_matrix  # Pre-normalized tag similarity
        self.extended_corpus_df = extended_corpus_df  # Answerer IDs
        self.alpha = alpha

    def transform(self, queries_df):
        final_scores_list = []

        for _, query_row in queries_df.iterrows():
            qid = query_row['qid']
            author_id = query_row['user_id']

            # Retrieve precomputed BM25 scores for this query
            query_bm25_scores = self.precomputed_bm25[self.precomputed_bm25['qid'] == qid]

            for _, row in query_bm25_scores.iterrows():
                docno = row['docno']
                bm25_score = row['normalized_score']  # Use pre-normalized BM25 score

                # Get the answerer's ID
                answerer_id = self.extended_corpus_df.loc[self.extended_corpus_df['docno'] == docno, 'answerer_id'].values[0]

                # Retrieve pre-normalized tag similarity score
                tag_similarity_score = self.normalized_tag_matrix.loc[author_id, answerer_id] if (author_id in self.normalized_tag_matrix.index) and (answerer_id in self.normalized_tag_matrix.columns) else 0

                # Combine scores
                final_score = self.alpha * bm25_score + (1 - self.alpha) * tag_similarity_score

                # Store result
                final_scores_list.append({'qid': qid, 'docno': docno, 'score': final_score})

        return pd.DataFrame(final_scores_list)


In [ ]:
combined_retriever = CombinedRetriever(precomputed_bm25_val, normalized_tag_matrix, extended_corpus_df, alpha=0.7)
combined_pipeline = pt.BatchRetrieve(index) >> combined_retriever

<ipython-input-152-144dc501d074>:2: DeprecationWarning: Call to deprecated class BatchRetrieve. (use pt.terrier.Retriever() instead) -- Deprecated since version 0.11.0.
  combined_pipeline = pt.BatchRetrieve(index) >> combined_retriever


In [ ]:
results = combined_retriever.transform(val_queries)

In [ ]:
results

qid             docno     score
0    academia_143743  workplace_102543  0.198229
1    academia_143743  philosophy_23588  0.146824
2    academia_143743          law_5712  0.122366
3    academia_143743       buddhism_64  0.121329
4    academia_143743   parenting_30739  0.195068
..               ...               ...       ...
967   politics_53742       money_69650  0.202027
968   politics_53742        health_933  0.167730
969   politics_53742         rpg_12464  0.083615
970   politics_53742         law_26574  0.378216
971   politics_53742       scifi_21220  0.072647

[972 rows x 3 columns]

In [ ]:
combined_results = pt.Experiment(
    [combined_pipeline],
    val_queries,
    val_qrels,
    names=["BM25 + Tag Similarity"],
    eval_metrics=["map", "ndcg", "P.1"]
)

In [ ]:
combined_results

name       map      ndcg  P.1
0  BM25 + Tag Similarity  0.572615  0.609104  0.5

Now we have to do two last things: check if we can implement the user presentations in the profile similarity scores, and finally use another grid search to compute the best weights for the pipeline.

#### User presentation attempt

The following is the users df with cleaned user presentations. We want to retrieve user presentations for questioners (users in val_queries) and for answerers (users in extended_corpus_df).

In [ ]:
users

user_id  user_reputation  user_profile_views  user_upvotes  \
0             -1                1                 151          5590   
1              1              101                 807             0   
2              2              101                   6             5   
3              3              101                   5             1   
4              4              101                  10             1   
...          ...              ...                 ...           ...   
2782727   163023                1                   0             0   
2782728   163024                1                   0             0   
2782729   163025                1                   0             0   
2782730   163026                1                   0             0   
2782731   163027                1                   0             0   

                                         user_presentation  
0        Hi, I'm not really a person. I'm a background ...  
1        Dev #2 who helped create Stack Overflow curren...  
2        Former Developer on the Stack Overflow team. W...  
3        co-founder of Airtable  formerly a dev at Stac...  
4        I used to design stuff for Stack Exchange. Als...  
...                                                    ...  
2782727                                                     
2782728  I'm studying Agriculture Mechatronics. And I r...  
2782729                                                     
2782730                                                     
2782731                                                     

[2782732 rows x 5 columns]

In [ ]:
val_queries_pers

qid                                              query  \
0      academia_143743      On answering a question that no one has asked   
1      academia_148899  How much domain expertise and network does a s...   
2          anime_56513  Does Overhaul need to touch with his hands to ...   
3          anime_59459         Why did Kanon reincarnate in another race?   
4         apple_408963     How do I disallow screen sharing for Messages?   
..                 ...                                                ...   
93      judaism_110801                   Where were Yaakov's sons buried?   
94  christianity_75499                  Is a Catholic canon a prebendary?   
95       gaming_363535    What does each statistic do in Dragon Quest XI?   
96      skeptics_47727  Did white supremacists "mix-in" with groups pr...   
97      politics_53742  Why do US police treat using counterfeit money...   

    user_id                                               tags  \
0   1582241            [publications, publishability, history]   
1    935589             [publications, editors, special-issue]   
2     59256                                 [my-hero-academia]   
3     59256                        [mao-gakuin-no-futekigosha]   
4    331923                         [security, screen-sharing]   
..      ...                                                ...   
93  4345338  [parshanut-torah-comment, shevatim-12-tribes, ...   
94  1582241                           [catholicism, canon-law]   
95   923667                                  [dragon-quest-xi]   
96  2516845                          [united-states, politics]   
97  3425570    [united-states, police, civil-rights, currency]   

                                    user_presentation  
0                                                      
1                                                      
2   Software Engineer with strong problem solving ...  
3   Software Engineer with strong problem solving ...  
4                      Life is too short for bad code  
..                                                ...  
93                                                     
94                                                     
95                                                     
96                                                     
97                                                     

[98 rows x 5 columns]

In [ ]:
val_users_presentation = val_queries_pers[['user_id', 'user_presentation']]
val_users_presentation = val_users_presentation.groupby('user_id').agg({
    'user_presentation': lambda x: max(x, key=len)  # Keep the set with the most tags
}).reset_index()

val_users_presentation

user_id                                  user_presentation
0       1325  Cgvector here. Live in UK. Graphic designer wi...
1       7879                                                   
2      17355                      I am not actually Von Kaiser.
3      22370                                                   
4      30494                                                   
5      59256  Software Engineer with strong problem solving ...
6      67390  I live. I do stuff. That's what makes me uniqu...
7      69157                                                   
8     210795                                                   
9     331923                     Life is too short for bad code
10    359320                                                   
11    507522                                                   
12    906366                                                   
13    923667                                                   
14    935589                                                   
15    961274                                                   
16   1068606                                                   
17   1077413                                                   
18   1344292                                                   
19   1352706                                                   
20   1532620                                                   
21   1582241                                                   
22   1634774                                                   
23   1821810                                                   
24   2150876                                                   
25   2293919                                                   
26   2516845                                                   
27   2580331                                                   
28   2614901                                                   
29   3305982                                                   
30   3425570                                                   
31   3690277                                                   
32   3832028                                                   
33   3972996                                                   
34   4345338                                                   
35   4403071                                                   
36   6362904                                                   
37   9101990                                                   
38  11680930                                                   
39  12194021

We already know this is not going to help much, but we can always redistribute weights in case one of the scores is missing (we cannot compute it).

In [ ]:
total_answerers['answerer_id'] = total_answerers['answerer_id'].astype(int)

<ipython-input-161-b0706e6f33c0>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  total_answerers['answerer_id'] = total_answerers['answerer_id'].astype(int)


In [ ]:
total_answerers

answerer_id
0           74379
1          507794
2          528857
3          114006
5          342002
...           ...
9388      2950649
9390      1550338
9392     11182787
9395      6848536
9397      1110667

[3689 rows x 1 columns]

The following step would be to retrieve user presentations for each answerer too, but in an attempt to merge, we realized there may be some duplicate values, or better different presentations associated with the same user_id.

Indeed, we discoreved the following:

In [ ]:
users[users['user_id'] == 1]

user_id  user_reputation  user_profile_views  user_upvotes  \
1              1              101                 807             0   
141780         1              101                  76             0   
152849         1              101                  11             0   
252851         1              101                  35             0   
262181         1              101                 447             0   
298468         1              101                1167             8   
529171         1              101                1326             0   
565498         1              101                 708             1   
612728         1              101                 909             0   
630869         1              101                1088            14   
661143         1              101                 363             0   
702505         1              101                  49             2   
777691         1              101                3030             2   
944042         1              101                 244             1   
1009698        1              101                 443             0   
1099968        1              101                 625             0   
1129141        1              101                 202             1   
1142699        1              101                 996             0   
1183563        1              101                1578             1   
1238515        1              101                 110             1   
1257680        1              101                  51             0   
1489171        1             1537                  32            15   
1537961        1              346                  43            15   
2141591        1              101                 289             0   
2608769        1              101                3488             0   

                                         user_presentation  
1        Dev #2 who helped create Stack Overflow curren...  
141780   Developer at Stack Overflow focusing on public...  
152849   Developer at Stack Overflow focusing on public...  
252851   I am a Principal Software Engineer at Microsof...  
262181   Dev #2 who helped create Stack Overflow curren...  
298468   Dev #2 who helped create Stack Overflow curren...  
529171   Dev #2 who helped create Stack Overflow curren...  
565498   I am a Principal Software Engineer at Microsof...  
612728   Dev #2 who helped create Stack Overflow curren...  
630869   Dev #2 who helped create Stack Overflow curren...  
661143   Dev #2 who helped create Stack Overflow curren...  
702505   Developer at Stack Overflow focusing on public...  
777691   Dev #2 who helped create Stack Overflow curren...  
944042   Developer at Stack Overflow focusing on public...  
1009698  Developer at Stack Overflow focusing on public...  
1099968  Developer at Stack Overflow focusing on public...  
1129141  Developer at Stack Overflow focusing on public...  
1142699  Dev #2 who helped create Stack Overflow curren...  
1183563  Developer at Stack Overflow focusing on public...  
1238515  Developer at Stack Overflow focusing on public...  
1257680  I am a Principal Software Engineer at Microsof...  
1489171  I am a experienced Web Developer. I have knowl...  
1537961  Developer at Stack Overflow focusing on public...  
2141591  Developer at Stack Overflow focusing on public...  
2608769  Dev #2 who helped create Stack Overflow curren...

In [ ]:
users[users['user_id'] == 3]

user_id  user_reputation  user_profile_views  user_upvotes  \
3              3              101                   5             1   
42193          3            19171                1412           244   
141781         3             4166                  69            54   
152851         3                1                   4             0   
156930         3              101                  22             1   
252853         3              101                   3             0   
298470         3              101                  19             7   
346555         3              101                  41             4   
469435         3              101                  40             9   
529173         3              101                  15             5   
565500         3              101                   5             3   
612730         3             1920                 120           105   
630871         3              101                  12             3   
661145         3              101                  10             2   
702507         3              101                   3             0   
714372         3             1772                 242            16   
777693         3              101                  17             0   
847382         3            31494                9490         11719   
935183         3              243                   5            11   
944044         3              709                  58            10   
955571         3              101                   6             0   
981614         3               99                  21             4   
1009700        3              757                  16            20   
1045942        3            23340                1083          4027   
1066270        3              101                  20             0   
1099970        3               92                 500            10   
1129143        3              101                   9             0   
1142701        3              101                   9             0   
1183565        3              333                  76            13   
1204576        3              101                  12             0   
1238517        3              101                  11             4   
1257682        3              101                   5             3   
1267206        3              101                   3             0   
1292569        3             8498                1346          2344   
1489173        3              631                  13            11   
1511175        3              101                   3             0   
1537963        3              101                   4             0   
1553193        3               98                  52            92   
1919276        3              101                  12             0   
2035863        3              231                 117           220   
2106664        3              101                  32             1   
2141593        3              101                   9             0   
2156405        3              101                   8            66   
2186022        3              101                  11             8   
2234944        3              252                 269            17   
2608771        3              101                  33             0   
2654974        3             3512                 293          4568   

                                         user_presentation  
3        co-founder of Airtable  formerly a dev at Stac...  
42193    Professionally, I'm a software engineer focusi...  
141781                                                      
152851                                                   .  
156930   I am a Principal Software Engineer at Microsof...  
252853   Developer at Stack Overflow focusing on public...  
298470   I am a Principal Software Engineer at Microsof...  
346555   I am a Principal Software Engineer at Microsof...  
469435   Officially voted World's Okayest Boss by a

In [ ]:
users[users['user_id'] == 608]

user_id  user_reputation  user_profile_views  user_upvotes  \
453          608              353                  13             3   
42781        608              103                   3          1409   
142364       608              193                   3             2   
153417       608              101                   0             0   
157496       608              483                  36             4   
253415       608               21                   1             0   
262707       608              201                   3             8   
277708       608              105                  52            21   
298909       608                1                   1             0   
347068       608              101                   0             4   
469872       608              101                  21             0   
566060       608              101                   0             6   
613289       608              101                   1             2   
631375       608              101                   1             0   
661722       608              101                   0            17   
679746       608              101                   0             0   
703074       608              101                   0             1   
714953       608              101                  24            61   
778262       608              101                   7             1   
935752       608              101                   0             0   
944603       608              101                   1            43   
956135       608              101                   0             0   
1010266      608              615                  82            64   
1046262      608              213                   4             2   
1066764      608              101                   1             0   
1129713      608              101                   0            10   
1205108      608               51                   0             0   
1239080      608              101                   1             0   
1258204      608               31                   3             0   
1267784      608             2854                 379            60   
1293082      608              195                  24            33   
1489748      608              101                   0             0   
1511677      608              101                   2             0   
1538540      608              101                   0             1   
1553717      608              383                  25            34   
1919797      608              123                   3            30   
2107208      608              288                  18            35   
2156903      608              538                  14           218   
2186508      608              486                  18             9   
2235416      608              420                  33           113   
2655518      608              101                   0             7   

                                         user_presentation  
453                                                         
42781                                                       
142364                                                      
153417   FLOSS fan and Geany developer.  And ... #SOrea...  
157496                                                      
253415                                                      
262707                                                      
277708                                                      
298909    Manifold GIS and database programming enthusiast  
347068   I use technology to create stuff that makes li...  
469872   Rob Eisenberg is a JavaScript expert, .NET arc...  
566060   Just a newbie, not very knowledgeable or exper...  
613289                                                      
631375   A developer working for a smallish software ho...  
661722                                                      
679746   My home is MS Windows-free, I work with U

This makes it impossible to include user presentations as a condition for profile similarity, because there is no way of choosing which version to keep for each user! Unfortunately, we have to abstain from this, and simply continue with the grid search.

#### Weight tuning

Since the user presentation method demonstrated to be fruitless, we can go on to perform grid search on the weight parameters for the hybrid personalized model.

In [ ]:
# Define alpha values to search
alpha_values = [i / 10 for i in range(11)]

# Store results
results = []

# Perform grid search for alpha
for alpha in alpha_values:
    combined_retriever = CombinedRetriever(precomputed_bm25_val, normalized_tag_matrix, extended_corpus_df, alpha=alpha)
    combined_pipeline = pt.BatchRetrieve(index) >> combined_retriever

    # Evaluate the pipeline
    experiment = pt.Experiment(
        [combined_pipeline],
        val_queries,
        val_qrels,
        names=[f"alpha={alpha}"],
        eval_metrics=["map", "ndcg", "P.1"]
    )

    # Store results
    results.append((alpha, experiment.iloc[0]['map'], experiment.iloc[0]['ndcg'], experiment.iloc[0]['P.1']))

# Find the best alpha based on P.1
best_alpha = max(results, key=lambda x: x[3])[0]
print(f"Best alpha: {best_alpha}")

<ipython-input-22-568197e6d2ec>:10: DeprecationWarning: Call to deprecated class BatchRetrieve. (use pt.terrier.Retriever() instead) -- Deprecated since version 0.11.0.
  combined_pipeline = pt.BatchRetrieve(index) >> combined_retriever
<ipython-input-22-568197e6d2ec>:10: DeprecationWarning: Call to deprecated class BatchRetrieve. (use pt.terrier.Retriever() instead) -- Deprecated since version 0.11.0.
  combined_pipeline = pt.BatchRetrieve(index) >> combined_retriever
<ipython-input-22-568197e6d2ec>:10: DeprecationWarning: Call to deprecated class BatchRetrieve. (use pt.terrier.Retriever() instead) -- Deprecated since version 0.11.0.
  combined_pipeline = pt.BatchRetrieve(index) >> combined_retriever
<ipython-input-22-568197e6d2ec>:10: DeprecationWarning: Call to deprecated class BatchRetrieve. (use pt.terrier.Retriever() instead) -- Deprecated since version 0.11.0.
  combined_pipeline = pt.BatchRetrieve(index) >> combined_retriever
<ipython-input-22-568197e6d2ec>:10: DeprecationWarni

This computes the best weights for the hybrid personalization model, considering precision@1 as metric.